In [1]:
import numpy as np
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import descartes 
import seaborn as sns
import plotly.express as px
import re

In [2]:
# Importanmos el archivo a usar
df = pd.read_csv("./properatti.csv")

In [3]:
df.head(5)

Unnamed: 0 operation property_type place_name  \
0           0      sell            PH  Mataderos   
1           1      sell     apartment   La Plata   
2           2      sell     apartment  Mataderos   
3           3      sell            PH    Liniers   
4           4      sell     apartment     Centro   

                             place_with_parent_names country_name  \
0              |Argentina|Capital Federal|Mataderos|    Argentina   
1        |Argentina|Bs.As. G.B.A. Zona Sur|La Plata|    Argentina   
2              |Argentina|Capital Federal|Mataderos|    Argentina   
3                |Argentina|Capital Federal|Liniers|    Argentina   
4  |Argentina|Buenos Aires Costa Atlántica|Mar de...    Argentina   

                     state_name  geonames_id                  lat-lon  \
0               Capital Federal    3430787.0  -34.6618237,-58.5088387   
1        Bs.As. G.B.A. Zona Sur    3432039.0  -34.9038831,-57.9643295   
2               Capital Federal    3430787.0  -34.6522615,-58.5229825   
3               Capital Federal    3431333.0  -34.6477969,-58.5164244   
4  Buenos Aires Costa Atlántica    3435548.0  -38.0026256,-57.5494468   

         lat  ...  surface_covered_in_m2  price_usd_per_m2 price_per_m2  \
0 -34.661824  ...                   40.0       1127.272727  1550.000000   
1 -34.903883  ...                    NaN               NaN          NaN   
2 -34.652262  ...                   55.0       1309.090909  1309.090909   
3 -34.647797  ...                    NaN               NaN          NaN   
4 -38.002626  ...                   35.0       1828.571429  1828.571429   

   floor  rooms  expenses                                      properati_url  \
0    NaN    NaN       NaN  http://www.properati.com.ar/15bo8_venta_ph_mat...   
1    NaN    NaN       NaN  http://www.properati.com.ar/15bob_venta_depart...   
2    NaN    NaN       NaN  http://www.properati.com.ar/15bod_venta_depart...   
3    NaN    NaN       NaN  http://www.properati.com.ar/15boh_venta_ph_lin...   
4    NaN    NaN       NaN  http://www.properati.com.ar/15bok_venta_depart...   

                                         description  \
0  2 AMBIENTES TIPO CASA PLANTA BAJA POR PASILLO,...   
1  Venta de departamento en décimo piso al frente...   
2  2 AMBIENTES 3ER PISO LATERAL LIVING COMEDOR AM...   
3  PH 3 ambientes con patio. Hay 3 deptos en lote...   
4  DEPARTAMENTO CON FANTÁSTICA ILUMINACIÓN NATURA...   

                                               title  \
0                 2 AMB TIPO CASA SIN EXPENSAS EN PB   
1  VENTA Depto 2 dorm. a estrenar 7 e/ 36 y 37   ...   
2           2 AMB 3ER PISO CON ASCENSOR APTO CREDITO   
3                       PH 3 amb. cfte. reciclado      
4  DEPTO 2 AMB AL CONTRAFRENTE ZONA CENTRO/PLAZA ...   

                                     image_thumbnail  
0  https://thumbs4.properati.com/8/BluUYiHJLhgIIK...  
1  https://thumbs4.properati.com/7/ikpVBu2ztHA7jv...  
2  https://thumbs4.properati.com/5/SXKr34F_IwG3W_...  
3  https://thumbs4.properati.com/3/DgIfX-85Mog5SP...  
4  https://thumbs4.properati.com/5/xrRqlNcSI_vs-f...  

[5 rows x 26 columns]

In [4]:
print("\x1b[1;33m"+"--------------------------------")
print("\x1b[1;33m"+"Shape", df.shape)
print("\x1b[1;33m"+"--------------------------------")
print("\x1b[1;33m"+"Columnas y sus tipos", df.dtypes)
print("\x1b[1;33m"+"--------------------------------")

--------------------------------
Shape (121220, 26)
--------------------------------
Columnas y sus tipos Unnamed: 0                      int64
operation                      object
property_type                  object
place_name                     object
place_with_parent_names        object
country_name                   object
state_name                     object
geonames_id                   float64
lat-lon                        object
lat                           float64
lon                           float64
price                         float64
currency                       object
price_aprox_local_currency    float64
price_aprox_usd               float64
surface_total_in_m2           float64
surface_covered_in_m2         float64
price_usd_per_m2              float64
price_per_m2                  float64
floor                         float64
rooms                         float64
expenses                      float64
properati_url                  object
description         

In [5]:
#Como vemos, da igual, por lo que pasamos a borrarla.
df = df.drop(["Unnamed: 0"], axis=1)
df.sample(2)

operation property_type     place_name  \
80014      sell     apartment  Palermo Chico   
48040      sell     apartment      San Telmo   

                                 place_with_parent_names country_name  \
80014  |Argentina|Capital Federal|Palermo|Palermo Chico|    Argentina   
48040              |Argentina|Capital Federal|San Telmo|    Argentina   

            state_name  geonames_id                        lat-lon        lat  \
80014  Capital Federal          NaN  -34.5776782468,-58.4126446918 -34.577678   
48040  Capital Federal    3428113.0        -34.6211839,-58.3731163 -34.621184   

             lon  ...  surface_covered_in_m2 price_usd_per_m2  price_per_m2  \
80014 -58.412645  ...                  126.0      4500.000000   5000.000000   
48040 -58.373116  ...                   29.0      2291.612727  46496.551724   

       floor  rooms  expenses  \
80014    NaN    NaN   12000.0   
48040    NaN    1.0       NaN   

                                           properati_url  \
80014  http://www.properati.com.ar/1awb7_venta_depart...   
48040  http://www.properati.com.ar/199hx_venta_depart...   

                                             description  \
80014  Exclusivo piso de 140m2 totales (126 cubiertos...   
48040  Edificio en construcción En una de las avenida...   

                                                   title  \
80014  Exclusivo piso de 140m2 con cochera y dependen...   
48040  Ubicado sobre una de las avenidas más emblemát...   

                                         image_thumbnail  
80014  https://thumbs4.properati.com/7/BzYCPtCAEYXwGq...  
48040  https://thumbs4.properati.com/3/HVEq4hsxJCBUAW...  

[2 rows x 25 columns]

In [6]:
#Borro la columna "operation" porque todas son ventas.
df = df.drop(["operation"], axis=1)
df.head(3)

property_type place_name                      place_with_parent_names  \
0            PH  Mataderos        |Argentina|Capital Federal|Mataderos|   
1     apartment   La Plata  |Argentina|Bs.As. G.B.A. Zona Sur|La Plata|   
2     apartment  Mataderos        |Argentina|Capital Federal|Mataderos|   

  country_name              state_name  geonames_id                  lat-lon  \
0    Argentina         Capital Federal    3430787.0  -34.6618237,-58.5088387   
1    Argentina  Bs.As. G.B.A. Zona Sur    3432039.0  -34.9038831,-57.9643295   
2    Argentina         Capital Federal    3430787.0  -34.6522615,-58.5229825   

         lat        lon     price  ... surface_covered_in_m2  \
0 -34.661824 -58.508839   62000.0  ...                  40.0   
1 -34.903883 -57.964330  150000.0  ...                   NaN   
2 -34.652262 -58.522982   72000.0  ...                  55.0   

   price_usd_per_m2  price_per_m2  floor  rooms  expenses  \
0       1127.272727   1550.000000    NaN    NaN       NaN   
1               NaN           NaN    NaN    NaN       NaN   
2       1309.090909   1309.090909    NaN    NaN       NaN   

                                       properati_url  \
0  http://www.properati.com.ar/15bo8_venta_ph_mat...   
1  http://www.properati.com.ar/15bob_venta_depart...   
2  http://www.properati.com.ar/15bod_venta_depart...   

                                         description  \
0  2 AMBIENTES TIPO CASA PLANTA BAJA POR PASILLO,...   
1  Venta de departamento en décimo piso al frente...   
2  2 AMBIENTES 3ER PISO LATERAL LIVING COMEDOR AM...   

                                               title  \
0                 2 AMB TIPO CASA SIN EXPENSAS EN PB   
1  VENTA Depto 2 dorm. a estrenar 7 e/ 36 y 37   ...   
2           2 AMB 3ER PISO CON ASCENSOR APTO CREDITO   

                                     image_thumbnail  
0  https://thumbs4.properati.com/8/BluUYiHJLhgIIK...  
1  https://thumbs4.properati.com/7/ikpVBu2ztHA7jv...  
2  https://thumbs4.properati.com/5/SXKr34F_IwG3W_...  

[3 rows x 24 columns]

In [7]:
# Drop column "lat-lon" porque es repetitiva
df = df.drop(["lat-lon"], axis=1)
df

property_type       place_name  \
0                 PH        Mataderos   
1          apartment         La Plata   
2          apartment        Mataderos   
3                 PH          Liniers   
4          apartment           Centro   
...              ...              ...   
121215     apartment         Belgrano   
121216         house           Beccar   
121217     apartment    Villa Urquiza   
121218     apartment      Plaza Colón   
121219     apartment  Capital Federal   

                                  place_with_parent_names country_name  \
0                   |Argentina|Capital Federal|Mataderos|    Argentina   
1             |Argentina|Bs.As. G.B.A. Zona Sur|La Plata|    Argentina   
2                   |Argentina|Capital Federal|Mataderos|    Argentina   
3                     |Argentina|Capital Federal|Liniers|    Argentina   
4       |Argentina|Buenos Aires Costa Atlántica|Mar de...    Argentina   
...                                                   ...          ...   
121215               |Argentina|Capital Federal|Belgrano|    Argentina   
121216  |Argentina|Bs.As. G.B.A. Zona Norte|San Isidro...    Argentina   
121217          |Argentina|Capital Federal|Villa Urquiza|    Argentina   
121218  |Argentina|Buenos Aires Costa Atlántica|Mar de...    Argentina   
121219                        |Argentina|Capital Federal|    Argentina   

                          state_name  geonames_id        lat        lon  \
0                    Capital Federal    3430787.0 -34.661824 -58.508839   
1             Bs.As. G.B.A. Zona Sur    3432039.0 -34.903883 -57.964330   
2                    Capital Federal    3430787.0 -34.652262 -58.522982   
3                    Capital Federal    3431333.0 -34.647797 -58.516424   
4       Buenos Aires Costa Atlántica    3435548.0 -38.002626 -57.549447   
...                              ...          ...        ...        ...   
121215               Capital Federal    3436077.0        NaN        NaN   
121216      Bs.As. G.B.A. Zona Norte    3436080.0        NaN        NaN   
121217               Capital Federal    3433775.0 -34.570639 -58.475596   
121218  Buenos Aires Costa Atlántica          NaN        NaN        NaN   
121219               Capital Federal    3433955.0        NaN        NaN   

           price currency  ...  surface_covered_in_m2  price_usd_per_m2  \
0        62000.0      USD  ...                   40.0       1127.272727   
1       150000.0      USD  ...                    NaN               NaN   
2        72000.0      USD  ...                   55.0       1309.090909   
3        95000.0      USD  ...                    NaN               NaN   
4        64000.0      USD  ...                   35.0       1828.571429   
...          ...      ...  ...                    ...               ...   
121215  870000.0      USD  ...                   93.0       7699.115044   
121216  498000.0      USD  ...                  360.0       1383.333333   
121217  131500.0      USD  ...                   39.0       2858.695652   
121218   95900.0      USD  ...                   48.0       1997.916667   
121219  129000.0      USD  ...                   77.0       1675.324675   

        price_per_m2  floor  rooms  expenses  \
0        1550.000000    NaN    NaN       NaN   
1                NaN    NaN    NaN       NaN   
2        1309.090909    NaN    NaN       NaN   
3                NaN    NaN    NaN       NaN   
4        1828.571429    NaN    NaN       NaN   
...              ...    ...    ...       ...   
121215   9354.838710    NaN    NaN   10000.0   
121216   1383.333333    NaN    NaN       NaN   
121217   3371.794872    NaN    NaN       NaN   
121218   1997.916667    NaN    NaN       NaN   
121219   1675.324675    NaN    NaN    3500.0   

                                            properati_url  \
0       http://www.properati.com.ar/15bo8_venta_ph_mat...   
1       http://www.properati.com.ar/15bob_venta_depart...   
2       http://www.properati.com.ar/15bod_venta_depart...   
3 

In [8]:
# Deseamos conocer el porcentaje de nulos por columna;
porcentaje_nulos_por_columna= (pd.isna(df).sum()/len(df))*100
round(porcentaje_nulos_por_columna.sort_values(ascending=False),2)

floor                         93.48
expenses                      88.23
rooms                         60.91
price_usd_per_m2              43.39
lat                           42.53
lon                           42.53
surface_total_in_m2           32.44
price_per_m2                  27.69
currency                      16.84
price_aprox_usd               16.84
price                         16.84
price_aprox_local_currency    16.84
surface_covered_in_m2         16.42
geonames_id                   15.44
image_thumbnail                2.57
place_name                     0.02
description                    0.00
title                          0.00
properati_url                  0.00
state_name                     0.00
country_name                   0.00
place_with_parent_names        0.00
property_type                  0.00
dtype: float64

In [9]:
# Revisamos el porcentaje de propiedades que hay en cada región.
state_name_mix = (df["state_name"].value_counts()/len(df)).reset_index()
state_name_mix['state_name'] = (state_name_mix['state_name']*100).round(1) 
state_name_mix.columns = ['state_name', 'mix']
state_name_mix

state_name   mix
0                Capital Federal  26.7
1       Bs.As. G.B.A. Zona Norte  21.1
2         Bs.As. G.B.A. Zona Sur  11.5
3                        Córdoba  10.0
4                       Santa Fe   8.4
5   Buenos Aires Costa Atlántica   8.3
6       Bs.As. G.B.A. Zona Oeste   7.7
7          Buenos Aires Interior   1.9
8                      Río Negro   0.7
9                        Neuquén   0.6
10                       Mendoza   0.6
11                       Tucumán   0.6
12                    Corrientes   0.5
13                      Misiones   0.4
14                    Entre Ríos   0.3
15                         Salta   0.2
16                        Chubut   0.2
17                      San Luis   0.2
18                      La Pampa   0.1
19                       Formosa   0.1
20                         Chaco   0.0
21                      San Juan   0.0
22              Tierra Del Fuego   0.0
23                     Catamarca   0.0
24                         Jujuy   0.0
25                    Santa Cruz   0.0
26           Santiago Del Estero   0.0
27                      La Rioja   0.0

In [10]:
# Graficamos la cantidad de propiedades por provincia

fig = px.bar(data_frame = state_name_mix[state_name_mix["mix"] >1.8], x='state_name' , y='mix', text='mix' , width=500, height=500)

fig.update_layout(
    title='<b>Propiedades por Provincia</b>',
    xaxis_tickfont_size=10,
    yaxis=dict(title='% del total',titlefont_size=14,tickfont_size=10),
    title_x=0.5)
fig.update_traces(textposition='inside', textangle = 0, insidetextanchor='middle')

fig.show()

In [11]:
#Calculamos la cantidad de datos que van a quedar fuera en el nuevo df por tener pocos datos.
state_name_mix_menor_1_9 = state_name_mix[state_name_mix["mix"]<1.9]["state_name"].tolist()

df.loc[df["state_name"].isin(state_name_mix_menor_1_9),:].shape

(5532, 23)

In [12]:
#Sort dataframe by columns

df_column_sorted = {
    "floor": df["floor"],
    "expenses": df["expenses"],
    "rooms": df["rooms"],
    "price_usd_per_m2": df["price_usd_per_m2"],
    "lon": df["lon"],
    "lat": df["lat"],
    "surface_total_in_m2": df["surface_total_in_m2"],
    "currency": df["currency"],
    "price_aprox_usd": df["price_aprox_usd"],
    "price_aprox_local_currency": df["price_aprox_local_currency"],
    "price": df["price"],
    "surface_covered_in_m2": df["surface_covered_in_m2"],
    "place_name": df["place_name"],
    "geonames_id": df["geonames_id"],
    "state_name": df["state_name"],
    "title": df["title"],
    "description": df["description"],
    "property_type": df["property_type"]
}

df = pd.DataFrame(df_column_sorted)

In [13]:
df = df.set_index("state_name")

In [14]:
#Antes de hacer el count de abajo, quiero, en esta línea, dejar sólo los registros iguales a:
state_name_list_ok = ["Capital Federal",
"Bs.As. G.B.A. Zona Norte",
"Bs.As. G.B.A. Zona Sur",
"Córdoba",
"Santa Fe",
"Buenos Aires Costa Atlántica",
"Bs.As. G.B.A. Zona Oeste",
"Buenos Aires Interior"]

In [15]:
df.shape

(121220, 17)

In [16]:
df.loc[state_name_list_ok, :].shape

(115688, 17)

In [17]:
# df con los datos de los 8 state_name más importantes.
df = df.loc[state_name_list_ok, :]

In [18]:
# Vemos los valores de mean y max de apartment porque nos habíamos encontrado con números de 2mil para arriba;
df.groupby(["state_name", "property_type"]).describe().loc["Capital Federal"]

floor                                                      \
                count       mean        std  min  25%  50%    75%     max   
property_type                                                               
PH              155.0   2.251613   2.211521  1.0  1.0  1.0   3.00    16.0   
apartment      2838.0  13.243834  84.696737  1.0  2.0  4.0   7.00  2509.0   
house             8.0  10.875000   7.395703  2.0  6.0  9.5  14.00    26.0   
store             8.0   9.375000  10.979689  1.0  2.0  3.0  15.25    31.0   

              expenses               ... surface_covered_in_m2            \
                 count         mean  ...                   75%       max   
property_type                        ...                                   
PH               182.0   962.730769  ...                 115.0    1183.0   
apartment       6196.0  6634.878631  ...                  79.0  187000.0   
house             12.0  2675.916667  ...                 320.0    8175.0   
store            202.0  2896.549505  ...                 231.0   10958.0   

              geonames_id                                                     \
                    count          mean            std        min        25%   
property_type                                                                  
PH                 1766.0  3.529494e+06  556658.475395  3427366.0  3429422.0   
apartment         25950.0  3.530139e+06  555737.593268  3427366.0  3429760.0   
house              2021.0  3.469355e+06  345993.449956  3427366.0  3430114.0   
store              1293.0  3.578327e+06  675300.520405  3427366.0  3429595.0   

                                                
                     50%        75%        max  
property_type                                   
PH             3430787.0  3433955.0  6693230.0  
apartment      3433775.0  3436003.0  6693230.0  
house          3433910.0  3433955.0  6693230.0  
store          3430787.0  3435548.0  6693230.0  

[4 rows x 96 columns]

In [19]:
#Vemos la cantidad de no nulos en la columna floor para todos los datos.
df.loc[df["floor"].notnull()].describe()

floor      expenses        rooms  price_usd_per_m2          lon  \
count  7615.000000   1027.000000  5441.000000       3208.000000  5905.000000   
mean     17.403152   2522.842259     2.647307       2340.929008   -59.683618   
std     116.985284   2481.155954     1.271013        868.641196     2.270634   
min       1.000000      1.000000     1.000000         29.906933   -75.678931   
25%       1.000000   1200.000000     2.000000       1857.142857   -60.639286   
50%       3.000000   1800.000000     3.000000       2239.436620   -58.478612   
75%       6.000000   2869.000000     3.000000       2787.656423   -58.423104   
max    2509.000000  19000.000000    22.000000      19800.000000   -56.674305   

               lat  surface_total_in_m2  price_aprox_usd  \
count  5905.000000          3595.000000     6.795000e+03   
mean    -33.928174            81.444228     2.251617e+05   
std       1.488243           245.697695     3.037610e+05   
min     -38.583214            10.000000     0.000000e+00   
25%     -34.618785            45.000000     9.200000e+04   
50%     -34.589013            60.000000     1.380000e+05   
75%     -32.957491            84.000000     2.250000e+05   
max       4.545843          9563.000000     3.900000e+06   

       price_aprox_local_currency         price  surface_covered_in_m2  \
count                6.795000e+03  6.795000e+03            6898.000000   
mean                 3.972866e+06  3.527507e+05              99.895332   
std                  5.359711e+06  6.354222e+05             325.831184   
min                  0.000000e+00  0.000000e+00               1.000000   
25%                  1.623294e+06  1.020000e+05              44.000000   
50%                  2.434941e+06  1.500000e+05              60.000000   
75%                  3.970012e+06  2.710000e+05              93.000000   
max                  6.881355e+07  1.168104e+07           12731.000000   

        geonames_id  
count  6.812000e+03  
mean   3.635403e+06  
std    5.406267e+05  
min    3.427326e+06  
25%    3.429651e+06  
50%    3.433955e+06  
75%    3.838574e+06  
max    6.942539e+06

In [20]:
df["floor"].sort_values(ascending=False).head(40)

state_name
Capital Federal             2509.0
Bs.As. G.B.A. Zona Norte    2177.0
Capital Federal             2103.0
Bs.As. G.B.A. Zona Norte    1609.0
Bs.As. G.B.A. Zona Norte    1609.0
Bs.As. G.B.A. Zona Norte    1609.0
Bs.As. G.B.A. Zona Norte    1609.0
Bs.As. G.B.A. Zona Norte    1608.0
Bs.As. G.B.A. Zona Norte    1608.0
Bs.As. G.B.A. Zona Norte    1607.0
Bs.As. G.B.A. Zona Norte    1606.0
Bs.As. G.B.A. Zona Norte    1602.0
Bs.As. G.B.A. Zona Norte    1512.0
Bs.As. G.B.A. Zona Norte    1504.0
Bs.As. G.B.A. Zona Norte    1504.0
Bs.As. G.B.A. Zona Norte    1450.0
Bs.As. G.B.A. Zona Norte    1420.0
Bs.As. G.B.A. Zona Norte    1407.0
Bs.As. G.B.A. Zona Norte    1404.0
Bs.As. G.B.A. Zona Norte    1403.0
Bs.As. G.B.A. Zona Norte    1401.0
Bs.As. G.B.A. Zona Norte    1379.0
Bs.As. G.B.A. Zona Norte    1306.0
Bs.As. G.B.A. Zona Norte    1305.0
Bs.As. G.B.A. Zona Norte    1304.0
Bs.As. G.B.A. Zona Norte    1301.0
Bs.As. G.B.A. Zona Norte    1291.0
Bs.As. G.B.A. Zona Norte    1208.0
Bs.As. G.

In [21]:
#Cantidad de datos no nulos en floor.
df["floor"].count()

7615

In [22]:
# Buscamos el dato del edificio más grande de arg que tiene 54 pisos.
df["floor"][df["floor"] > 54].count()

180

In [23]:
df.reset_index(inplace=True)

In [24]:
# Rescatamos el index de todos los que son mayores a 54.
indices_mayor_54_floor = df[df["floor"] > 54].index

In [25]:
indices_mayor_54_floor = indices_mayor_54_floor.tolist()

In [26]:
# porcentaje de los valores outliers de floor mayores a 54.
outliers_floor_mayores_a_54 = 180/7615*100
print("\x1b[1;33m"+"Porcentaje outliers floor mayores a 54 pisos: " ,outliers_floor_mayores_a_54)

Porcentaje outliers floor mayores a 54 pisos:  2.3637557452396587


In [27]:
# La cantidad de datos erróneos en la columna floor respecto a la cantidad total de datos.
print("\x1b[1;33m"+"cantidad de datos erróneos en la columna floor respecto a la cantidad total de datos:", 180/df.shape[0]*100)

cantidad de datos erróneos en la columna floor respecto a la cantidad total de datos: 0.1555908996611576


In [28]:
# Imputamos los datos mayores a 54 de la columna floor por apartment con NAN.
df["floor"].where(df["floor"] < 54, np.NAN, inplace=True)

In [29]:
# Verificamos que los 180 datos que tenían datos erróneos en la columna floor, fueron reemplazados por NAN.
df[df.index.isin(indices_mayor_54_floor)].head(3)

state_name  floor  expenses  rooms  price_usd_per_m2        lon  \
984   Capital Federal    NaN       NaN    2.0               NaN -58.479707   
1269  Capital Federal    NaN       NaN    3.0               NaN -58.472350   
1270  Capital Federal    NaN       NaN    4.0               NaN -58.472617   

            lat  surface_total_in_m2 currency  price_aprox_usd  \
984  -34.566330                  NaN      USD         175000.0   
1269 -34.575419                  NaN      NaN              NaN   
1270 -34.575560                  NaN      NaN              NaN   

      price_aprox_local_currency     price  surface_covered_in_m2  \
984                    3087787.5  175000.0                   65.0   
1269                         NaN       NaN                    NaN   
1270                         NaN       NaN                    NaN   

         place_name  geonames_id  \
984   Villa Urquiza    3433775.0   
1269       Belgrano    3436077.0   
1270       Belgrano    3436077.0   

                                                  title  \
984   2 AMB BALCÓN CON PARRILLA - EDIFICIO CON AMENI...   
1269    LA PAMPA AL 4300, Exclusivo Desarrollo en Pesos   
1270              LA PAMPA 4300 AIR PAMPA POZO EN PESOS   

                                            description property_type  
984   Corredor Responsable: Rebeca Stern - C.U.C.I.C...     apartment  
1269  Corredor Responsable: Raul Hector Merlo - CUCI...     apartment  
1270  Corredor Responsable: Raul Hector Merlo - CUCI...     apartment

In [30]:
# Pensamos en imputar los datos que son casas con valores de 0, porque tienen piso cero, de ahí empezamos a hacer el siguiente análisis:

# Contamos la cantidad de registros que son casas.
df_house = df.loc[df["property_type"] == "house"]
# print("Cantidad de registros que son casas del df: ", df_house, sep="")

pd.DataFrame(df_house)

state_name  floor  expenses  rooms  price_usd_per_m2  \
13            Capital Federal    NaN       NaN    NaN        875.000000   
15            Capital Federal    NaN       NaN    NaN       1091.269841   
26            Capital Federal    NaN       NaN    NaN        944.444444   
27            Capital Federal    NaN       NaN    NaN        658.602151   
28            Capital Federal    NaN       NaN    NaN        611.111111   
...                       ...    ...       ...    ...               ...   
115678  Buenos Aires Interior    NaN       NaN    5.0        400.801603   
115680  Buenos Aires Interior    NaN       NaN    4.0        747.782267   
115684  Buenos Aires Interior    NaN       NaN    5.0        172.839506   
115686  Buenos Aires Interior    NaN       NaN    4.0        192.307692   
115687  Buenos Aires Interior    NaN       NaN    NaN               NaN   

              lon        lat  surface_total_in_m2 currency  price_aprox_usd  \
13     -58.362056 -34.617719                 80.0      USD         70000.00   
15     -58.410702 -34.636321                504.0      USD        550000.00   
26            NaN        NaN                180.0      USD        170000.00   
27            NaN        NaN                744.0      USD        490000.00   
28            NaN        NaN                720.0      USD        440000.00   
...           ...        ...                  ...      ...              ...   
115678 -59.100573 -37.313734                499.0      USD        200000.00   
115680 -62.277651 -38.730753                 75.0      ARS         56083.67   
115684        NaN        NaN               1215.0      USD        210000.00   
115686 -58.259803 -37.837561                390.0      USD         75000.00   
115687        NaN        NaN                  NaN      USD        130000.00   

        price_aprox_local_currency      price  surface_covered_in_m2  \
13                      1235115.00    70000.0                   50.0   
15                      9704475.00   550000.0                  324.0   
26                      2999565.00   170000.0                  165.0   
27                      8645805.00   490000.0                  350.0   
28                      7763580.00   440000.0                  261.0   
...                            ...        ...                    ...   
115678                  3528900.00   200000.0                  156.0   
115680                   989568.31  1000000.0                   70.0   
115684                  3705345.00   210000.0                  250.0   
115686                  1323337.50    75000.0                  135.0   
115687                  2293785.00   130000.0                  105.0   

                  place_name  geonames_id  \
13             Puerto Madero    3429760.0   
15                     Boedo    3436003.0   
26           Capital Federal    3433955.0   
27           Capital Federal    3433955.0   
28           Capital Federal    3433955.0   
...                      ...          ...   
115678                Tandil    3427832.0   
115680          Bahía Blanca    3865084.0   
115684  Sierra de los Padres    3427958.0   
115686              Balcarce    3436176.0   
115687                 Luján    3430982.0   

                                                    title  \
13      FLOAT LIFE - CASA FLOTANTE - UBICABLE EN CLUBS...   
15              Casa impecable refaccionada! 6 ambientes.   
26      Casa 180m² con 2 Plantas en Navarro, Julián 29...   
27      Casa 744m² con 2 Plantas en Del Valle Iberluce...   
28      Casa 720m² con Plantas en Palma, Diego 1800, A...   
...                                                   ...   
115678                                         Casa venta   
115680                            Oportunidad Donado 1100   
115684                              Sierras de los Padres   
115686                           Casa+ Depto monoambiente   
115687                                Casa - Hosteria Sur   

                              

In [31]:
#Obtenemos el index de todos los datos que son casas:
indices_floor_house = df.loc[df["property_type"] == "house"].index.tolist()
# print("Indices de los registros que son casas: ", indices_floor_house)
print("\x1b[1;33m"+"Cantidad de datos house:", len(indices_floor_house))

Cantidad de datos house: 37554


In [32]:
# ¿Qué porcentaje representan las casas del total de registros?
print("\x1b[1;33m"+"Porcentaje de registros que son casas del df: ", df_house.shape[0] / df.shape[0] * 100," %", sep="")

Porcentaje de registros que son casas del df: 32.46144803263951 %


In [33]:
# Imputamos todos los registros de casas para que tengan en floor, valor 0 (cero)
df.loc[df["property_type"]=="house","floor"] = 0

In [34]:
# Verificamos que haya cambiado todos los valores a cero del paso anterior.
df[["property_type", "floor"]].head(50)

property_type  floor
0             PH    NaN
1      apartment    NaN
2             PH    NaN
3      apartment    NaN
4      apartment    NaN
5      apartment    NaN
6      apartment    NaN
7             PH    NaN
8      apartment    NaN
9      apartment    NaN
10     apartment    NaN
11     apartment    NaN
12     apartment    NaN
13         house    0.0
14     apartment    NaN
15         house    0.0
16     apartment    NaN
17     apartment    NaN
18     apartment    NaN
19     apartment    NaN
20         store    NaN
21     apartment    NaN
22     apartment    NaN
23     apartment    NaN
24     apartment    NaN
25     apartment    NaN
26         house    0.0
27         house    0.0
28         house    0.0
29         house    0.0
30     apartment   12.0
31         house    0.0
32            PH    1.0
33         house    0.0
34     apartment    NaN
35     apartment    6.0
36     apartment    NaN
37     apartment    NaN
38            PH    NaN
39     apartment    NaN
40            PH    NaN
41         store    NaN
42     apartment    NaN
43     apartment    NaN
44     apartment    NaN
45     apartment    NaN
46     apartment    NaN
47         store    NaN
48     apartment    NaN
49     apartment    NaN

In [35]:
# Verificamos que todos los registros con "property_type" == "house", ahora tengan "floor" == 0
df[df.index.isin(indices_floor_house)].head(3)

state_name  floor  expenses  rooms  price_usd_per_m2        lon  \
13  Capital Federal    0.0       NaN    NaN        875.000000 -58.362056   
15  Capital Federal    0.0       NaN    NaN       1091.269841 -58.410702   
26  Capital Federal    0.0       NaN    NaN        944.444444        NaN   

          lat  surface_total_in_m2 currency  price_aprox_usd  \
13 -34.617719                 80.0      USD          70000.0   
15 -34.636321                504.0      USD         550000.0   
26        NaN                180.0      USD         170000.0   

    price_aprox_local_currency     price  surface_covered_in_m2  \
13                   1235115.0   70000.0                   50.0   
15                   9704475.0  550000.0                  324.0   
26                   2999565.0  170000.0                  165.0   

         place_name  geonames_id  \
13    Puerto Madero    3429760.0   
15            Boedo    3436003.0   
26  Capital Federal    3433955.0   

                                                title  \
13  FLOAT LIFE - CASA FLOTANTE - UBICABLE EN CLUBS...   
15          Casa impecable refaccionada! 6 ambientes.   
26  Casa 180m² con 2 Plantas en Navarro, Julián 29...   

                                          description property_type  
13  ESTRUCTURA ECOLOGICA FLOTANTEIDEAL PARA UBICAR...         house  
15  Se encuentra dentro del Distrito Tecnológico. ...         house  
26  Casa en 2 Plantas en BÂ° La Merced, a Metros d...         house

In [36]:
# Vemos que luego de la imputación, bajó considerablemente la cantidad de nulos de la columna floor.
df.isnull().sum()

state_name                         0
floor                          71426
expenses                      101758
rooms                          69989
price_usd_per_m2               49058
lon                            48639
lat                            48639
surface_total_in_m2            37058
currency                       17871
price_aprox_usd                17870
price_aprox_local_currency     17870
price                          17870
surface_covered_in_m2          17744
place_name                        23
geonames_id                    18527
title                              0
description                        2
property_type                      0
dtype: int64

In [37]:
# Deseamos conocer el porcentaje de nulos por columna, vemos que el porcentaje de floor bajó considerablemente;
porcentaje_nulos_por_columna= (pd.isna(df).sum()/len(df))*100
round(porcentaje_nulos_por_columna.sort_values(ascending=False),2)

expenses                      87.96
floor                         61.74
rooms                         60.50
price_usd_per_m2              42.41
lat                           42.04
lon                           42.04
surface_total_in_m2           32.03
geonames_id                   16.01
currency                      15.45
price                         15.45
price_aprox_local_currency    15.45
price_aprox_usd               15.45
surface_covered_in_m2         15.34
place_name                     0.02
description                    0.00
property_type                  0.00
title                          0.00
state_name                     0.00
dtype: float64

In [38]:
# Analizamos cómo cambió la media, el std, y el max de floor luego de los cambios.
df.loc[(df["property_type"] == "apartment") & (df["state_name"] == "Capital Federal"), :].describe()

floor      expenses         rooms  price_usd_per_m2  \
count  2773.000000  6.196000e+03  13482.000000      19896.000000   
mean      4.955283  6.634879e+03      2.545097       3324.464870   
std       4.337346  1.796656e+05      1.439610       3892.824716   
min       1.000000  1.000000e+00      1.000000         31.369688   
25%       2.000000  1.200000e+03      1.000000       2111.111111   
50%       4.000000  2.000000e+03      2.000000       2566.046646   
75%       7.000000  3.900000e+03      3.000000       3168.758621   
max      43.000000  1.000150e+07     22.000000     206333.333333   

                lon           lat  surface_total_in_m2  price_aprox_usd  \
count  19446.000000  19446.000000         22580.000000     2.415400e+04   
mean     -58.433276    -34.599753            87.589017     2.453469e+05   
std        0.053687      0.037507          1332.550832     4.397744e+05   
min      -63.616672    -38.416097             0.000000     5.103610e+03   
25%      -58.461123    -34.619692            40.000000     9.901250e+04   
50%      -58.434144    -34.600369            56.000000     1.450000e+05   
75%      -58.402259    -34.580400            89.000000     2.500000e+05   
max      -58.354956    -34.534530        200000.000000     4.654544e+07   

       price_aprox_local_currency         price  surface_covered_in_m2  \
count                2.415400e+04  2.415400e+04           25240.000000   
mean                 4.329024e+06  3.706782e+05              79.353843   
std                  7.759600e+06  1.042946e+06            1183.327820   
min                  9.005064e+04  5.500000e+03               0.000000   
25%                  1.747026e+06  1.040905e+05              37.000000   
50%                  2.558452e+06  1.540000e+05              50.000000   
75%                  4.411125e+06  2.890000e+05              79.000000   
max                  8.212711e+08  5.000000e+07          187000.000000   

        geonames_id  
count  2.595000e+04  
mean   3.530139e+06  
std    5.557376e+05  
min    3.427366e+06  
25%    3.429760e+06  
50%    3.433775e+06  
75%    3.436003e+06  
max    6.693230e+06

In [39]:
# Total de datos diferentes a NaN y diferentes a cero, filtrados por departamentos.
dptos_dif_nan_y_cero = df.loc[(df["floor"] != 0) & (~np.isnan(df["floor"]))& (df["property_type"] == "apartment"), :].shape

print("\x1b[1;33m"+"(dptos) Total de datos diferentes a NaN y diferentes a cero: ", dptos_dif_nan_y_cero)

(dptos) Total de datos diferentes a NaN y diferentes a cero:  (6158, 18)


In [40]:
# Cantidad total de registros de dptos en el dataset.
dptos_all_shape = df.loc[df["property_type"] == "apartment"].shape
print("\x1b[1;33m"+"Cantidad total de registros de dptos en el dataset: ", dptos_all_shape)

Cantidad total de registros de dptos en el dataset:  (68740, 18)


In [41]:
# Porcentaje de registros de dptos en todo el dataset con valores distintos de cero y distintos de NaN, respecto al total de registros de dptos.
proporcion_dptos_not_nan_ni_cero_all_dptos = dptos_dif_nan_y_cero[0] / dptos_all_shape[0] * 100

print("\x1b[1;33m"+"Relación dptos not null ni cero respecto a total dptos: ", proporcion_dptos_not_nan_ni_cero_all_dptos)

Relación dptos not null ni cero respecto a total dptos:  8.958393948210649


Decición final sobre la columna "floor": Bye.

Motivo: La proporción de departamentos que no tienen valores cero ni NaN, respecto del total es demasiado baja para tomar decisiones al respecto.

In [42]:
# drop columna floor respecto a la conclusión de arriba;
df = df.drop(["floor"], axis=1) 
#--> Lo comentamos porque ya lo dropeamos y devuelve error;

In [43]:
# drop columna expenses por faltante de datos, no creemos que vaya a sumar al modelo;
df = df.drop(["expenses"], axis=1);  
# --> Lo comentamos porque ya lo dropeamos y devuelve error;


In [44]:
# drop de currency porque todas tienen la misma moneda;
df = df.drop(["currency"], axis=1)

In [45]:
# Revisamos el porcentaje de propiedades que hay por tipo.
property_type_mix = (df["property_type"].value_counts()/len(df)).reset_index()
property_type_mix['property_type'] = (property_type_mix['property_type']*100).round(1)
property_type_mix.columns = ['property_type', 'mix']
property_type_mix

property_type   mix
0     apartment  59.4
1         house  32.5
2            PH   4.8
3         store   3.3

In [46]:
# Graficamos el porcentaje por tipo de propiedad que hay en el DataFrame

fig = px.bar(data_frame= property_type_mix, x='property_type' , y='mix', text = 'mix'  , width=500, height=500)

fig.update_layout(
    title='<b>Propiedades por Tipo</b>',
    xaxis_tickfont_size=10,
    yaxis=dict(title='% del total',titlefont_size=14,tickfont_size=10),
    title_x=0.5)
fig.update_traces(textposition='inside', textangle = 0, insidetextanchor='middle')
fig.show()

# Desde acá en adelante empiezo a probar cosas sobre la columna price_usd_per_m2 

In [47]:
#Filtro el dataset para que me muestre solo las columnas sobre precios y m2.
df_price_and_m2 = df.loc[:,["price_usd_per_m2", "surface_total_in_m2", "price_aprox_usd", "price", "surface_covered_in_m2", "price_aprox_local_currency", "property_type", "state_name"]]

df_price_and_m2.head(5)

price_usd_per_m2  surface_total_in_m2  price_aprox_usd     price  \
0       1127.272727                 55.0          62000.0   62000.0   
1       1309.090909                 55.0          72000.0   72000.0   
2               NaN                  NaN          95000.0   95000.0   
3       3066.666667                 45.0         138000.0  138000.0   
4       3000.000000                 65.0         195000.0  195000.0   

   surface_covered_in_m2  price_aprox_local_currency property_type  \
0                   40.0                   1093959.0            PH   
1                   55.0                   1270404.0     apartment   
2                    NaN                   1676227.5            PH   
3                   40.0                   2434941.0     apartment   
4                   60.0                   3440677.5     apartment   

        state_name  
0  Capital Federal  
1  Capital Federal  
2  Capital Federal  
3  Capital Federal  
4  Capital Federal

In [48]:
#Cantidad de nulos por columna en cada una de las columnas de price y m2;
df_price_and_m2.isnull().sum().sort_values(ascending=False)

price_usd_per_m2              49058
surface_total_in_m2           37058
price_aprox_local_currency    17870
price                         17870
price_aprox_usd               17870
surface_covered_in_m2         17744
state_name                        0
property_type                     0
dtype: int64

In [49]:
#Cantidad total de registros;
df_price_and_m2.shape[0]

115688

In [50]:
# Proporción de nulls por columna según total de registros;
(df_price_and_m2.isnull().sum() / df_price_and_m2.shape[0] * 100).sort_values(ascending = False)

price_usd_per_m2              42.405435
surface_total_in_m2           32.032709
price_aprox_local_currency    15.446719
price                         15.446719
price_aprox_usd               15.446719
surface_covered_in_m2         15.337805
state_name                     0.000000
property_type                  0.000000
dtype: float64

In [51]:
# price_aprox_usd y price_aprox_local_currency tienen la misma cantidad de nulos 15.446719%, quiero ver si son los mismos registros;

# Reseteo el index porque necesito compararlos;
# df_price_and_m2.reset_index(inplace=True)

# Lo comento porque, sino, me agrega la columna index;

In [52]:
# Reseteamos el índice del df general también;
# df.reset_index(inplace=True)
# Lo comento porque, sino, me agrega la columna index;

In [53]:
# Verifico que el reset_index haya funcionado correctamente;
df_price_and_m2.head(2)

price_usd_per_m2  surface_total_in_m2  price_aprox_usd    price  \
0       1127.272727                 55.0          62000.0  62000.0   
1       1309.090909                 55.0          72000.0  72000.0   

   surface_covered_in_m2  price_aprox_local_currency property_type  \
0                   40.0                   1093959.0            PH   
1                   55.0                   1270404.0     apartment   

        state_name  
0  Capital Federal  
1  Capital Federal

In [54]:
#Guardo los índices de price_aprox_usd que son null en una lista;
index_price_aprox_usd_null = df_price_and_m2[df_price_and_m2["price_aprox_usd"].isnull()].index.tolist()

In [55]:
# Ahora rescato los indices de price_aprox_local_currency que son null;
index_price_aprox_local_currency_null = df_price_and_m2[df_price_and_m2["price_aprox_local_currency"].isnull()].index.tolist()

In [56]:
# Comparo las dos listas de índices de index_price_aprox_local_currency_null y index_price_aprox_usd_null para ver si son los mismso índices;

index_price_aprox_usd_null == index_price_aprox_local_currency_null

True

### Resolución:
<p>En un principio vimos que las columnas price_aprox_usd y price_aprox_local_currency presentaban la misma proporción de nulos, 15.446719%, al ser dos columnas de precio, donde una está sólo en dólares y la otra, en más de una moneda, como, por ejemplo, ARS, soles peruanos, pesos uruguayos, entre otros, decidimos que sería una buena idea estandarizar y usar dólares nada más, ahora, en la búsqueda de imputar el faltante de la columna en dólares, creímos que podríamos rescatar algo de la otra columna si es que no tenían los mismos registros con faltantes, pero no, resulta que, con la validación previa a este escrito, determinamos que se tratan de los mismos índices, por lo que lo único que resta hacer, es retirar la columna price_aprox_local_currency, lo cual lo realizamos a continuación.</p>

In [57]:
# Drop columna price_aprox_local_currency;
df = df.drop(["price_aprox_local_currency"], axis=1)

In [58]:
# Verificamos que se haya eliminado correctamente la columna price_aprox_local_currency;
df.head(2)

state_name  rooms  price_usd_per_m2        lon        lat  \
0  Capital Federal    NaN       1127.272727 -58.508839 -34.661824   
1  Capital Federal    NaN       1309.090909 -58.522982 -34.652262   

   surface_total_in_m2  price_aprox_usd    price  surface_covered_in_m2  \
0                 55.0          62000.0  62000.0                   40.0   
1                 55.0          72000.0  72000.0                   55.0   

  place_name  geonames_id                                     title  \
0  Mataderos    3430787.0        2 AMB TIPO CASA SIN EXPENSAS EN PB   
1  Mataderos    3430787.0  2 AMB 3ER PISO CON ASCENSOR APTO CREDITO   

                                         description property_type  
0  2 AMBIENTES TIPO CASA PLANTA BAJA POR PASILLO,...            PH  
1  2 AMBIENTES 3ER PISO LATERAL LIVING COMEDOR AM...     apartment

In [59]:
# Drop columna price_aprox_local_currency de df_price_and_m2;

df_price_and_m2 = df_price_and_m2.drop(["price_aprox_local_currency"], axis=1)

In [60]:
# Verificamos que se haya eliminado correctamente la columna price_aprox_local_currency de df_price_and_m2;
df_price_and_m2.head(2)

price_usd_per_m2  surface_total_in_m2  price_aprox_usd    price  \
0       1127.272727                 55.0          62000.0  62000.0   
1       1309.090909                 55.0          72000.0  72000.0   

   surface_covered_in_m2 property_type       state_name  
0                   40.0            PH  Capital Federal  
1                   55.0     apartment  Capital Federal


<br>
<hr>
<br>


### Siguiente paso: Realizar la misma verificación de recién, pero entre las columnas price_aprox_usd y price;

In [61]:
# Rescatamos los indices de price que son null;

index_price_null = df_price_and_m2[df_price_and_m2["price"].isnull()].index.tolist()

In [62]:
# Comparamos las dos listas de índices de index_price_null y index_price_aprox_usd_null para ver si son los mismso índices;
index_price_aprox_usd_null == index_price_null

True

### Resolución:
<p>La columna price tiene exactamente los mismos registros con faltantes que la columna price_aprox_usd, por lo que, siguiendo la misma lógica que utilizamos para eliminar la columna price_aprox_local_currency, decidimos eliminar la columna price, lo cuál, lo realizamos a continuación.</p>

In [63]:
# Eliminamos la columna price del df;
df = df.drop(["price"], axis=1)

In [64]:
# Verificamos que se haya borrado la columna price;
df.head(2)

state_name  rooms  price_usd_per_m2        lon        lat  \
0  Capital Federal    NaN       1127.272727 -58.508839 -34.661824   
1  Capital Federal    NaN       1309.090909 -58.522982 -34.652262   

   surface_total_in_m2  price_aprox_usd  surface_covered_in_m2 place_name  \
0                 55.0          62000.0                   40.0  Mataderos   
1                 55.0          72000.0                   55.0  Mataderos   

   geonames_id                                     title  \
0    3430787.0        2 AMB TIPO CASA SIN EXPENSAS EN PB   
1    3430787.0  2 AMB 3ER PISO CON ASCENSOR APTO CREDITO   

                                         description property_type  
0  2 AMBIENTES TIPO CASA PLANTA BAJA POR PASILLO,...            PH  
1  2 AMBIENTES 3ER PISO LATERAL LIVING COMEDOR AM...     apartment

In [65]:
# Eliminamos la columna price de df_price_and_m2;
df_price_and_m2 = df_price_and_m2.drop(["price"], axis=1)

In [66]:
# Verificamos que la columna price haya sido eliminada de df_price_and_m2;
df_price_and_m2.head(2)

price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
0       1127.272727                 55.0          62000.0   
1       1309.090909                 55.0          72000.0   

   surface_covered_in_m2 property_type       state_name  
0                   40.0            PH  Capital Federal  
1                   55.0     apartment  Capital Federal


<br>
<hr>
<br>


### Siguiente paso: Verificar si hay valores en la columna surface_covered_in_m2 que son mayores a surface_total_in_m2, de ser así, ver porqué es así, y determinar si hay que dropear o qué hay que hacer con esos datos;

In [67]:
# Volvemos a ver la proporción de nulls por columna según total de registros;
(df_price_and_m2.isnull().sum() / df_price_and_m2.shape[0] * 100).sort_values(ascending = False)

price_usd_per_m2         42.405435
surface_total_in_m2      32.032709
price_aprox_usd          15.446719
surface_covered_in_m2    15.337805
state_name                0.000000
property_type             0.000000
dtype: float64

In [68]:
# En el análisis que venimos haciendo, nos dimos cuenta que hay una relación entre price_usd_per_m2, surface_total_in_m2, price_aprox_usd y surface_covered_in_m2;
# Por este motivo, hicimos un groupby por state_name y property_type, con un describe, y vimos que habían varios datos muy grandes en varias columnas y std muy grandes y optamos por comenzar a limpiar esto;

pantallazo1 = df_price_and_m2.groupby(["state_name", "property_type"]).describe()["surface_covered_in_m2"]
pantallazo1

count        mean          std  \
state_name                   property_type                                     
Bs.As. G.B.A. Zona Norte     PH               909.0   85.288229    49.966955   
                             apartment       9839.0   74.610631   149.512375   
                             house          12533.0  247.839224   476.986116   
                             store            507.0  712.510848  2454.140063   
Bs.As. G.B.A. Zona Oeste     PH               648.0   88.967593   235.602048   
                             apartment       3091.0   54.716597   103.454012   
                             house           4000.0  174.512000   407.561039   
                             store            201.0  527.875622  2147.054715   
Bs.As. G.B.A. Zona Sur       PH               616.0   82.323052    64.858805   
                             apartment       4554.0   67.296882   148.303912   
                             house           5348.0  196.384256   317.003352   
                             store            422.0  537.620853  2140.200928   
Buenos Aires Costa Atlántica PH               398.0   92.778894   330.000643   
                             apartment       4772.0   75.220872   725.359366   
                             house           2165.0  193.356120   134.732137   
                             store            200.0  367.690000  1106.334336   
Buenos Aires Interior        PH                37.0   85.621622    43.722834   
                             apartment        629.0   76.774245   214.170626   
                             house           1061.0  211.642790   866.254308   
                             store             53.0  280.037736   286.216631   
Capital Federal              PH              1704.0   91.915493    66.348047   
                             apartment      25240.0   79.353843  1183.327820   
                             house           1856.0  248.990302   264.495649   
                             store           1177.0  263.112999   645.421746   
Córdoba                      PH               374.0   80.451872    46.148049   
                             apartment       4162.0   71.225853   188.490765   
                             house           3730.0  216.355764   258.923913   
                             store            341.0  440.639296  1544.264434   
Santa Fe                     PH                48.0   65.791667    46.138533   
                             apartment       6041.0   60.633173   109.382299   
                             house           1155.0  172.747186   467.001203   
                             store            133.0  175.947368   412.018908   

                                             min     25%    50%     75%  \
state_name                   property_type                                
Bs.As. G.B.A. Zona Norte     PH             14.0   55.00   78.0  105.00   
                             apartment       1.0   48.00   60.0   81.00   
                             house           1.0  150.00  209.0  296.00   
                             store           1.0   44.00  160.0  504.50   
Bs.As. G.B.A. Zona Oeste     PH              1.0   50.00   71.5   95.00   
                             apartment       1.0   37.00   44.0   60.00   
                             house           1.0   95.00  140.0  204.00   
                             store           1.0   40.00   86.0  333.00   
Bs.As. G.B.A. Zona Sur       PH              1.0   54.00   71.0  100.00   
                             apartment       1.0   43.00   54.0   75.00   
                             house           1.0  110.00  161.0  240.00   
                             store           1.0   35.00  131.0  320.00   
Buenos Aires Costa Atlántica PH             20.0   46.25   67.5   95.00   
                             apartment       1.0   40.00   52.0   75.00   
                             house           1.0  116.00  170.0  240.00   
                             store          12.0  

In [69]:
import json

pantallazo1_dict = {
    "PH": {
        "mean":pantallazo1["mean"][0].round(5),
        "std":pantallazo1["std"][0].round(5),
        "min":pantallazo1["min"][0].round(5),
        "max":pantallazo1["max"][0].round(5) 
        },
    "apartment": {
        "mean":pantallazo1["mean"][1].round(5),
        "std":pantallazo1["std"][1].round(5),
        "min":pantallazo1["min"][1].round(5),
        "max":pantallazo1["max"][1].round(5)
    },
    "house": {
        "mean":pantallazo1["mean"][2].round(5),
        "std":pantallazo1["std"][2].round(5),
        "min":pantallazo1["min"][2].round(5),
        "max":pantallazo1["max"][2].round(5) 
    },
    "store": {
        "mean":pantallazo1["mean"][3].round(5),
        "std":pantallazo1["std"][3].round(5),
        "min":pantallazo1["min"][3].round(5),
        "max":pantallazo1["max"][3].round(5)
    }
}

print("\x1b[1;33m"+"pantallazo1_dict es el resultado de un groupby de state_name y property_type, trayendo sólo la columna surface_covered_in_m2")
print("pantallazo1_dict:", json.dumps(pantallazo1_dict, indent=4))

# Del siguiente link saqué la info de cómo mostrar lindo un diccionario: https://stackoverflow.com/questions/44689546/how-to-print-out-a-dictionary-nicely-in-python

pantallazo1_dict es el resultado de un groupby de state_name y property_type, trayendo sólo la columna surface_covered_in_m2
pantallazo1_dict: {
    "PH": {
        "mean": 85.28823,
        "std": 49.96695,
        "min": 14.0,
        "max": 900.0
    },
    "apartment": {
        "mean": 74.61063,
        "std": 149.51238,
        "min": 1.0,
        "max": 10145.0
    },
    "house": {
        "mean": 247.83922,
        "std": 476.98612,
        "min": 1.0,
        "max": 38240.0
    },
    "store": {
        "mean": 712.51085,
        "std": 2454.14006,
        "min": 1.0,
        "max": 35000.0
    }
}


In [70]:
# Cantidad de datos nulos en la columna "surface_covered_in_m2";
df_price_and_m2.isnull()["surface_covered_in_m2"].sum()

17744

In [71]:
# Proporción de datos nulos en la columna "surface_covered_in_m2" respecto del total;
df_price_and_m2.isnull()["surface_covered_in_m2"].sum() / df_price_and_m2.shape[0] *100

15.337805131042112

In [72]:
# NAN de la columna surface_covered_in_m2;
df_price_and_m2.loc[np.isnan(df_price_and_m2["surface_covered_in_m2"]), :]

price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
2                    NaN                  NaN         95000.00   
23           1918.421053                 38.0         72900.00   
24                   NaN                  NaN         79851.93   
105          4212.121212                 33.0        139000.00   
127                  NaN                  NaN        130000.00   
...                  ...                  ...              ...   
115651        300.925926                432.0        130000.00   
115656               NaN                  NaN        220000.00   
115658               NaN                  NaN         78000.00   
115677       2373.913043                 92.0        218400.00   
115682               NaN                  NaN         75000.00   

        surface_covered_in_m2 property_type             state_name  
2                         NaN            PH        Capital Federal  
23                        NaN     apartment        Capital Federal  
24                        NaN     apartment        Capital Federal  
105                       NaN         store        Capital Federal  
127                       NaN     apartment        Capital Federal  
...                       ...           ...                    ...  
115651                    NaN         house  Buenos Aires Interior  
115656                    NaN         house  Buenos Aires Interior  
115658                    NaN     apartment  Buenos Aires Interior  
115677                    NaN     apartment  Buenos Aires Interior  
115682                    NaN     apartment  Buenos Aires Interior  

[17744 rows x 6 columns]

<hr>

In [73]:
# Hablamos con dos personas especialistas en inmobiliaria, dedicimos sacar los datos de casas con superficie cubierta de más de 2000m2 y dptos mayores a 800m2.

# En esta celda buscamos y listamos los índices de las propiedades house con un valor mayor a 2000 en surface_covered_in_m2;
df_price_and_m2_sin_house_mayor_2km2 = df_price_and_m2.loc[(df_price_and_m2["property_type"] == "house") & (df_price_and_m2["surface_covered_in_m2"] > 2000), :]

print("\x1b[1;33m"+"Cantidad de datos de casas con números de superficie cubierta mayor a 2k:", df_price_and_m2_sin_house_mayor_2km2.shape[0])

indices_df_price_and_m2_sin_house_mayor_2km2 = df_price_and_m2_sin_house_mayor_2km2.index.tolist()

print("\x1b[1;33m"+"indices df_price_and_m2_sin_house_mayor_2km2: ", indices_df_price_and_m2_sin_house_mayor_2km2)

df_price_and_m2_shape_0_before_drop = df_price_and_m2.shape[0]

Cantidad de datos de casas con números de superficie cubierta mayor a 2k: 32
indices df_price_and_m2_sin_house_mayor_2km2:  [2532, 14953, 34953, 35821, 37099, 38915, 40089, 40331, 41290, 41436, 42508, 43502, 44997, 45755, 51277, 57822, 61115, 62048, 67366, 71557, 72556, 72693, 74243, 83516, 84716, 85114, 102721, 104937, 108539, 113004, 114414, 114570]


In [74]:
# Dropeamos los registros de casas con superficie cubierta mayor a 2k en df_price_and_m2;
df_price_and_m2.drop(indices_df_price_and_m2_sin_house_mayor_2km2, axis=0, inplace=True)

In [75]:
# Cantidad de datos en df_price_and_m2 before modification:
print("\x1b[1;33m"+"Cantidad de datos en df_price_and_m2 before modification", df_price_and_m2_shape_0_before_drop)

Cantidad de datos en df_price_and_m2 before modification 115688


In [76]:
# Cantidad de datos a dropear en df_price_and_m2;
print("\x1b[1;33m"+"Cantidad de datos a dropear en df_price_and_m2:", len(indices_df_price_and_m2_sin_house_mayor_2km2))

Cantidad de datos a dropear en df_price_and_m2: 32


In [77]:
# Cantidad de datos after drop en en df_price_and_m2;
print("\x1b[1;33m"+"Cantidad de datos after drop en en df_price_and_m2", df_price_and_m2.shape[0])

Cantidad de datos after drop en en df_price_and_m2 115656


In [78]:
#Guardamos la cantida de datos before modif;
cantidad_de_datos_before_modif_house_mayor_2km2_drop = df.shape[0]

# Eliminamos los datos del df original;
df.drop(indices_df_price_and_m2_sin_house_mayor_2km2, axis=0, inplace=True)

In [79]:
#Cantida de datos antes de la modificación;
print("\x1b[1;33m"+"Cantidad de datos before modif: ", cantidad_de_datos_before_modif_house_mayor_2km2_drop)

Cantidad de datos before modif:  115688


In [80]:
# Cantidad de datos luego de la modificaicón;;
cantidad_de_datos_after_modif_house_mayor_2km2_drop = df.shape[0]
print("\x1b[1;33m", "Cantidad de datos after modif: ", cantidad_de_datos_after_modif_house_mayor_2km2_drop)

 Cantidad de datos after modif:  115656


In [81]:
# Cantidad de datos eliminados;
print("\x1b[1;33m"+"Cantidad de datos eliminados:", cantidad_de_datos_before_modif_house_mayor_2km2_drop - cantidad_de_datos_after_modif_house_mayor_2km2_drop)

Cantidad de datos eliminados: 32


In [82]:
# Verifico si todos los elementos mayores a 2k fueron eliminados correctamente, tenía dudas por los índices.
len(df.loc[(df["surface_covered_in_m2"] > 2000) & (df["property_type"] == "house"), :])

0

<hr>

In [83]:
# Vemos la cantidad de property_type=="apartment" que hay en total;
df_price_and_m2_total_apartment = df_price_and_m2.loc[df_price_and_m2["property_type"] == "apartment"]
print("\x1b[1;33m"+"En total hay: ", df_price_and_m2_total_apartment.shape[0], " departamentos.")

En total hay:  68740  departamentos.


In [84]:
# Del total de apartamentos, ¿Cuántos tienen un surface_covered_in_m2 > 800m2? --> Tomamos 800m2 porque, según una investigación que realizamos con especialistas, nos dijeron que el departamento más grande de Arg, tiene  800m2;

df_price_and_m2_total_apartment_mayor_800m2 = df_price_and_m2_total_apartment.loc[df_price_and_m2_total_apartment["surface_covered_in_m2"] > 800, :].sort_values("surface_covered_in_m2", ascending=False)

print("\x1b[1;33m"+"Cantidad de departamentos con surface_covered_in_m2 > 800m2: ", df_price_and_m2_total_apartment_mayor_800m2.shape[0])

df_price_and_m2_total_apartment_mayor_800m2


Cantidad de departamentos con surface_covered_in_m2 > 800m2:  52


price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
20644                NaN                  NaN        600000.00   
98185        1423.076923                 52.0         74000.00   
34321                NaN                  NaN        250000.00   
97080                NaN                  NaN        110000.00   
14875                NaN                  NaN        138000.00   
61932                NaN                  NaN         26359.32   
72629                NaN                 45.0              NaN   
17203                NaN                  NaN        220000.00   
88619                NaN                  NaN         47110.28   
28525                NaN                  NaN        108000.00   
30109                NaN                  NaN        129000.00   
73037                NaN               5500.0              NaN   
40207                NaN                  NaN        135000.00   
1294                 NaN                  NaN        140000.00   
115388        525.784453                128.0         67300.41   
109680               NaN                  NaN         75000.00   
60416                NaN                  NaN         81321.33   
74419                NaN                  NaN        170000.00   
42162        2358.490566                 53.0        125000.00   
90747        1563.871731                 52.0         81321.33   
73296          13.950649               5729.0         79923.27   
43250                NaN                  NaN        110000.00   
41751                NaN                  NaN         50194.89   
101329         14.562275               5837.0         85000.00   
30633                NaN                  NaN         72000.00   
7495                 NaN                  NaN         89000.00   
7474         2533.333333                 75.0        190000.00   
33685                NaN                  NaN         37576.06   
28500                NaN                  NaN         79952.88   
11705                NaN                  NaN         70000.00   
15169                NaN                  NaN         20190.12   
16869                NaN                  NaN         76900.00   
108383        349.997050                200.0         69999.41   
80322                NaN               2000.0              NaN   
95786         641.360414                314.0        201387.17   
72620                NaN               1700.0              NaN   
73103                NaN                  NaN         85000.00   
99356        1500.000000               1600.0       2400000.00   
83474                NaN                  NaN        790000.00   
80304                NaN               1233.0              NaN   
99382        1754.838710                155.0        272000.00   
42811         637.886598                776.0        495000.00   
72061                NaN               7500.0              NaN   
83472                NaN                  NaN         42062.75   
60209         150.000000               1000.0        150000.00   
44906         148.500000               1000.0        148500.00   
11908        3081.399339                121.0        372849.32   
84874                NaN                  NaN        151912.28   
16516                NaN                950.0              NaN   
45047          62.765957                940.0         59000.00   
99886                NaN                  NaN        160000.00   
42807          29.906933               9563.0        286000.00   

        surface_covered_in_m2 property_type                    state_name  
20644                187000.0     apartment               Capital Federal  
98185                 49000.0     apartment  Buenos Aires Costa Atlántica  
34321                 10145.0     apartment      Bs.As. G.B.A. Zona Norte  
97080                  9435.0     apartment  Buenos Aires Costa Atlántica  
14875                  9152.0     apartment               Capital Federal  
61932                  8225.0     apartment        Bs

In [85]:
# Buscamos el índice de los departamentos que tienen surface_covered_in_m2 > 800;
index_df_price_and_m2_total_apartment_mayor_800m2 = df_price_and_m2_total_apartment_mayor_800m2.index.tolist()
print("\x1b[1;33m"+"Longitud de la lista de indices to drop: ", len(index_df_price_and_m2_total_apartment_mayor_800m2))

Longitud de la lista de indices to drop:  52


In [86]:
# Dropeamos de df_price_and_m2 los registros de dptos que tienen surface_covered_in_m2 > 800;
df_price_and_m2.drop(index_df_price_and_m2_total_apartment_mayor_800m2, axis=0, inplace=True)

In [87]:
# Cantidad de dptos antes:
print("\x1b[1;33m"+"Cantidad de dptos before drop: ", len(df_price_and_m2_total_apartment))

Cantidad de dptos before drop:  68740


In [88]:
# Cantidad de datos a borrar:
print("\x1b[1;33m"+"Cantidad de dptos to drop: ", len(index_df_price_and_m2_total_apartment_mayor_800m2))

Cantidad de dptos to drop:  52


In [89]:
# Verificamos que se hayan borrado correctamente;
print("\x1b[1;33m"+"Cantidad de dptos after drop: ",len(df_price_and_m2_total_apartment) - len(index_df_price_and_m2_total_apartment_mayor_800m2))
print("\033[4;35;47m"+"Los datos se han eliminado correctamente."+'\033[0;m')

Cantidad de dptos after drop:  68688
Los datos se han eliminado correctamente.


In [90]:
# Validamos que no haya quedado ningún dato apartment con surface_covered_in_m2 > 800;

df_price_and_m2_cant_apartment_surface_covered_in_m2_mayor_800 = len(df_price_and_m2.loc[(df_price_and_m2["surface_covered_in_m2"] > 800) & (df_price_and_m2["property_type"] == "apartment"), :])
print("\x1b[1;33m"+"La cantidad de registros apartment con surface_covered_in_m2 > 800 que quedaron luego del drop en df_price_and_m2 es de: ", df_price_and_m2_cant_apartment_surface_covered_in_m2_mayor_800)

# Hacemos un if que avise si se borraron correctamente los datos;
if df_price_and_m2_cant_apartment_surface_covered_in_m2_mayor_800 == 0:
    print("\033[4;35;47m"+"Los datos se han eliminado correctamente."+'\033[0;m')

La cantidad de registros apartment con surface_covered_in_m2 > 800 que quedaron luego del drop en df_price_and_m2 es de:  0
Los datos se han eliminado correctamente.


In [91]:
# Ahora dropeamos del df original los registros de dptos que tienen surface_covered_in_m2 > 800 
df.drop(index_df_price_and_m2_total_apartment_mayor_800m2, axis=0, inplace=True);

#--> Le pongo ; a la línea anterior para que no muestre el resultado, solo lo elimine;

In [92]:
# Verificamos que se hayan borrado correctamente los datos;
df_cant_apartment_surface_covered_in_m2_mayor_800 = len(df.loc[(df["surface_covered_in_m2"] > 800) & (df["property_type"] == "apartment")])

print("\x1b[1;33m"+"La cantidad de registros apartment con surface_covered_in_m2 > 800 que quedaron luego del drop en df original es de: ", df_cant_apartment_surface_covered_in_m2_mayor_800)

# Hacemos un condicional que avise si los datos se borraron correctamente;
if df_cant_apartment_surface_covered_in_m2_mayor_800 == 0:
    print("\033[4;35;47m"+"Los datos se han eliminado correctamente."+'\033[0;m')

La cantidad de registros apartment con surface_covered_in_m2 > 800 que quedaron luego del drop en df original es de:  0
Los datos se han eliminado correctamente.


In [93]:
# Chequeamos los valores de mean, std y max para apartment y house en "Bs.As.G.B.A Zona Norte" que lo tomamos como referencia;
pantallazo2 = df_price_and_m2.groupby(["state_name", "property_type"]).describe()["surface_covered_in_m2"]

pantallazo2

count        mean          std  \
state_name                   property_type                                     
Bs.As. G.B.A. Zona Norte     PH               909.0   85.288229    49.966955   
                             apartment       9829.0   71.012819    43.508323   
                             house          12519.0  238.058791   144.490842   
                             store            507.0  712.510848  2454.140063   
Bs.As. G.B.A. Zona Oeste     PH               648.0   88.967593   235.602048   
                             apartment       3089.0   52.432502    31.970093   
                             house           3997.0  165.112584   108.990251   
                             store            201.0  527.875622  2147.054715   
Bs.As. G.B.A. Zona Sur       PH               616.0   82.323052    64.858805   
                             apartment       4551.0   64.190288    39.773057   
                             house           5344.0  189.793413   125.778744   
                             store            422.0  537.620853  2140.200928   
Buenos Aires Costa Atlántica PH               398.0   92.778894   330.000643   
                             apartment       4765.0   61.137041    36.025785   
                             house           2164.0  192.405730   127.297762   
                             store            200.0  367.690000  1106.334336   
Buenos Aires Interior        PH                37.0   85.621622    43.722834   
                             apartment        628.0   68.401274    42.128437   
                             house           1059.0  182.813975   144.701460   
                             store             53.0  280.037736   286.216631   
Capital Federal              PH              1704.0   91.915493    66.348047   
                             apartment      25225.0   69.601388    56.928402   
                             house           1854.0  242.632147   167.454990   
                             store           1177.0  263.112999   645.421746   
Córdoba                      PH               374.0   80.451872    46.148049   
                             apartment       4151.0   63.670441    41.957406   
                             house           3726.0  210.970478   141.023607   
                             store            341.0  440.639296  1544.264434   
Santa Fe                     PH                48.0   65.791667    46.138533   
                             apartment       6038.0   58.628023    33.125615   
                             house           1153.0  153.773634   101.935173   
                             store            133.0  175.947368   412.018908   

                                             min     25%    50%     75%  \
state_name                   property_type                                
Bs.As. G.B.A. Zona Norte     PH             14.0   55.00   78.0  105.00   
                             apartment       1.0   48.00   60.0   81.00   
                             house           1.0  150.00  209.0  295.00   
                             store           1.0   44.00  160.0  504.50   
Bs.As. G.B.A. Zona Oeste     PH              1.0   50.00   71.5   95.00   
                             apartment       1.0   37.00   44.0   60.00   
                             house           1.0   95.00  140.0  203.00   
                             store           1.0   40.00   86.0  333.00   
Bs.As. G.B.A. Zona Sur       PH              1.0   54.00   71.0  100.00   
                             apartment       1.0   43.00   54.0   75.00   
                             house           1.0  110.00  161.0  240.00   
                             store           1.0   35.00  131.0  320.00   
Buenos Aires Costa Atlántica PH             20.0   46.25   67.5   95.00   
                             apartment       1.0   40.00   52.0   74.00   
                             house           1.0  116.00  169.5  240.00   
                             store          12.0  

In [116]:
pantallazo2_dict = {
    "PH": {
        "mean":pantallazo2["mean"][0].round(5),
        "std":pantallazo2["std"][0].round(5),
        "min":pantallazo2["min"][0].round(5),
        "max":pantallazo2["max"][0].round(5) 
        },
    "apartment": {
        "mean":pantallazo2["mean"][1].round(5),
        "std":pantallazo2["std"][1].round(5),
        "min":pantallazo2["min"][1].round(5),
        "max":pantallazo2["max"][1].round(5)
    },
    "house": {
        "mean":pantallazo2["mean"][2].round(5),
        "std":pantallazo2["std"][2].round(5),
        "min":pantallazo2["min"][2].round(5),
        "max":pantallazo2["max"][2].round(5) 
    },
    "store": {
        "mean":pantallazo2["mean"][3].round(5),
        "std":pantallazo2["std"][3].round(5),
        "min":pantallazo2["min"][3].round(5),
        "max":pantallazo2["max"][3].round(5)
    }
}

print("\x1b[1;33m"+"pantallazo2_dict es el resultado de un groupby de state_name y property_type, trayendo sólo la columna surface_covered_in_m2")
print("pantallazo2_dict:", json.dumps(pantallazo2_dict, indent=4))

pantallazo2_dict es el resultado de un groupby de state_name y property_type, trayendo sólo la columna surface_covered_in_m2
pantallazo2_dict: {
    "PH": {
        "mean": 85.28823,
        "std": 49.96695,
        "min": 14.0,
        "max": 900.0
    },
    "apartment": {
        "mean": 71.01282,
        "std": 43.50832,
        "min": 1.0,
        "max": 755.0
    },
    "house": {
        "mean": 238.05879,
        "std": 144.49084,
        "min": 1.0,
        "max": 1800.0
    },
    "store": {
        "mean": 712.51085,
        "std": 2454.14006,
        "min": 1.0,
        "max": 35000.0
    }
}


In [133]:
# Las acciones que hemos llevado a cabo, lo hicimos para sacar números incorrectos de tamaño de superficie cubierta en property_type == house y en property_type == apartment, para que sea más coherente y reducir la media, el std y el max;

pantallazo1_mean = pantallazo1_dict["apartment"]["mean"]
pantallazo2_mean = pantallazo2_dict["apartment"]["mean"]
print("pantallazo1_mean:", pantallazo1_mean)
print("pantallazo2_mean:",pantallazo2_mean)
print(f"La media en apartment la hemos reducido: {(pantallazo1_mean-pantallazo2_mean).round(4)} puntos")
print("----------------------------------------------------")

pantallazo1_std = pantallazo1_dict["apartment"]["std"]
pantallazo2_std = pantallazo2_dict["apartment"]["std"]
print("pantallazo1_std:", pantallazo1_std)
print("pantallazo2_std:",pantallazo2_std)
print(f"La media en apartment la hemos reducido: {(pantallazo1_std-pantallazo2_std).round(4)} puntos")
print("----------------------------------------------------")

pantallazo1_max = pantallazo1_dict["apartment"]["max"]
pantallazo2_max = pantallazo2_dict["apartment"]["max"]
print("pantallazo1_max:", pantallazo1_max)
print("pantallazo2_max:",pantallazo2_max)
print(f"La media en apartment la hemos reducido: {(pantallazo1_max-pantallazo2_max).round(4)} puntos")
print("----------------------------------------------------")

pantallazo1_mean: 74.61063
pantallazo2_mean: 71.01282
La media en apartment la hemos reducido: 3.5978 puntos
----------------------------------------------------
pantallazo1_std: 149.51238
pantallazo2_std: 43.50832
La media en apartment la hemos reducido: 106.0041 puntos
----------------------------------------------------
pantallazo1_max: 10145.0
pantallazo2_max: 755.0
La media en apartment la hemos reducido: 9390.0 puntos
----------------------------------------------------


In [96]:
# Tenemos que empezar a limpiar los mínimos por tipo de propiedad también, en cada columna;

In [97]:
# Chequeamos el std respecto al anterior. --> Falta ver de cuánto era antes y ver cómo cambió en proporción;
df_price_and_m2.groupby(["property_type"]).describe()["surface_covered_in_m2"]

count        mean          std  min    25%    50%     75%  \
property_type                                                                
PH              4734.0   87.844106   139.850537  1.0   52.0   74.0  105.00   
apartment      58276.0   66.242364    47.872314  0.0   40.0   52.0   75.00   
house          31816.0  209.883455   139.116000  1.0  120.0  180.0  260.00   
store           3034.0  417.252802  1578.684550  1.0   41.0  116.0  297.25   

                   max  
property_type           
PH              6610.0  
apartment        792.0  
house           2000.0  
store          35000.0

In [98]:
# Datos donde superficie cubierta es mayor a superficie total;
df_price_and_m2.loc[df_price_and_m2["surface_covered_in_m2"] > df_price_and_m2["surface_total_in_m2"]]

price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
82           3440.000000                125.0         430000.0   
83           3440.000000                125.0         430000.0   
354          1850.000000                 80.0         148000.0   
569                  NaN                 34.0              NaN   
1120         1944.444444                144.0         280000.0   
...                  ...                  ...              ...   
114826        850.000000                100.0          85000.0   
114972       1285.714286                280.0         360000.0   
115090       2931.034483                 58.0         170000.0   
115143               NaN                522.0              NaN   
115606       1666.666667                375.0         625000.0   

        surface_covered_in_m2 property_type             state_name  
82                      156.0         house        Capital Federal  
83                      156.0         house        Capital Federal  
354                      89.0     apartment        Capital Federal  
569                      36.0     apartment        Capital Federal  
1120                    147.0     apartment        Capital Federal  
...                       ...           ...                    ...  
114826                  150.0         house  Buenos Aires Interior  
114972                  332.0         house  Buenos Aires Interior  
115090                   59.0     apartment  Buenos Aires Interior  
115143                  700.0         store  Buenos Aires Interior  
115606                  625.0         house  Buenos Aires Interior  

[1047 rows x 6 columns]

In [99]:
df_price_and_m2_surface_covered_m2_sorted = df_price_and_m2.sort_values("surface_covered_in_m2", ascending= False)

df_price_and_m2_surface_covered_m2_sorted.head(50)

price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
48168                NaN                 35.0              NaN   
70553          64.516129              93000.0        6000000.0   
113331               NaN              25186.0              NaN   
76507          72.000000              25000.0        1800000.0   
54453                NaN              22355.0              NaN   
63658                NaN                  NaN              NaN   
63565         219.512195              20500.0        4500000.0   
48073                NaN              20000.0              NaN   
50764                NaN              18375.0              NaN   
101964        514.285714              14000.0        7200000.0   
48036         606.060606              13200.0        8000000.0   
111004               NaN                  NaN        9000000.0   
47883         556.506849              11680.0        6500000.0   
18031         775.688994              10958.0        8500000.0   
110917        317.073171               8200.0        2600000.0   
48012         240.000000              10000.0        2400000.0   
17583        1036.001036               7722.0        8000000.0   
47942         763.157895               7600.0        5800000.0   
62377         168.302945               7130.0        1200000.0   
63103         428.571429               7000.0        3000000.0   
99643        1000.000000                100.0         100000.0   
47795                NaN               6500.0              NaN   
47364                NaN               6500.0              NaN   
47970                NaN               6500.0              NaN   
110888       1048.387097               6200.0        6500000.0   
80149                NaN               6000.0              NaN   
69014         700.000000               6000.0        4200000.0   
110697       1603.448276                 58.0          93000.0   
22905         846.623351               5079.0        4300000.0   
78905                NaN                  NaN        2300000.0   
48081         640.000000               5000.0        3200000.0   
52691         647.511129               4942.0        3200000.0   
62786        1048.951049               4290.0        4500000.0   
62780        1048.951049               4290.0        4500000.0   
48217                NaN                  NaN        3500000.0   
17447         833.333333               4800.0        4000000.0   
18027        1354.166667               4800.0        6500000.0   
80246                NaN               4760.0              NaN   
80247                NaN               4760.0              NaN   
80462                NaN               4700.0              NaN   
62390         543.478261               4600.0        2500000.0   
17501          24.207190               4590.0         111111.0   
17451                NaN                  NaN        5000000.0   
62388         555.555556               4500.0        2500000.0   
110859        459.770115               4350.0        2000000.0   
17700          26.273587               4229.0         111111.0   
62386                NaN                  NaN        2000000.0   
63708         376.884422               3980.0        1500000.0   
80588                NaN               3900.0              NaN   
112613       1142.334933               4377.0        5000000.0   

        surface_covered_in_m2 property_type                    state_name  
48168                 35000.0         store      Bs.As. G.B.A. Zona Norte  
70553                 30000.0         store        Bs.As. G.B.A. Zona Sur  
113331                25186.0         store      Bs.As. G.B.A. Zona Oeste  
76507                 25000.0         store                       Córdoba  
54453                 22355.0         store      Bs.As. G.B.A. Zona Norte  
63658                 19826.0         store        Bs.As. G.B.A. Zona Sur  
63565                 19609.0         store        Bs.As. G.B.A. Zona Sur  
48073                 19200.0    

In [100]:
# Graficamos los precios por M2 en usd por tipo de propiedad

fig = px.scatter(data_frame = df_price_and_m2_surface_covered_m2_sorted, x = "property_type", y = "price_usd_per_m2", size_max = 10, 
               width=700, height=500)

fig.update_layout(
    title='<b>Precio por M2 en USD por tipo de propiedad</b>')
fig.show()

In [101]:
df.sort_values("surface_covered_in_m2", ascending= False)

state_name  rooms  price_usd_per_m2        lon  \
48168   Bs.As. G.B.A. Zona Norte    NaN               NaN        NaN   
70553     Bs.As. G.B.A. Zona Sur    NaN         64.516129 -58.425045   
113331  Bs.As. G.B.A. Zona Oeste    NaN               NaN -58.530716   
76507                    Córdoba    NaN         72.000000        NaN   
54453   Bs.As. G.B.A. Zona Norte    NaN               NaN        NaN   
...                          ...    ...               ...        ...   
115651     Buenos Aires Interior    NaN        300.925926 -57.902854   
115656     Buenos Aires Interior    NaN               NaN        NaN   
115658     Buenos Aires Interior    NaN               NaN -62.270166   
115677     Buenos Aires Interior    NaN       2373.913043        NaN   
115682     Buenos Aires Interior    NaN               NaN -62.262843   

              lat  surface_total_in_m2  price_aprox_usd  \
48168         NaN                 35.0              NaN   
70553  -34.781917              93000.0        6000000.0   
113331 -34.638347              25186.0              NaN   
76507         NaN              25000.0        1800000.0   
54453         NaN              22355.0              NaN   
...           ...                  ...              ...   
115651 -34.922468                432.0         130000.0   
115656        NaN                  NaN         220000.0   
115658 -38.712532                  NaN          78000.0   
115677        NaN                 92.0         218400.0   
115682 -38.718968                  NaN          75000.0   

        surface_covered_in_m2       place_name  geonames_id  \
48168                 35000.0      Tortuguitas          NaN   
70553                 30000.0  Lomas de Zamora    3431270.0   
113331                25186.0        Ciudadela    3435376.0   
76507                 25000.0          Córdoba    3860255.0   
54453                 22355.0            Munro    3430511.0   
...                       ...              ...          ...   
115651                    NaN          Berisso    3436038.0   
115656                    NaN          Ranchos    3429610.0   
115658                    NaN     Bahía Blanca    3865084.0   
115677                    NaN            Luján    3430982.0   
115682                    NaN     Bahía Blanca    3865084.0   

                                                    title  \
48168                       Nave Industrial - Tortuguitas   
70553   LAVALLOL. Predio Industrial de 93.000 m2 y 30....   
113331                     Edificio Comercial - Ciudadela   
76507   Excelente nave industrial, Planta de Silo y Mo...   
54453                             Nave Industrial - Munro   
...                                                   ...   
115651   Casa Amplia con Cochera y Dto interno con Patio    
115656                                     Casa - Ranchos   
115658                                     Caronti Nº 108   
115677                     Departamento - Centro De Lujan   
115682                          Venta dto 1 dorm céntrico   

                                              description property_type  
48168   Plaza Logística Tortugas CÓDIGO 0703 T35.000 m...         store  
70553   CODIGO: 2484-FB0007 ubicado en: Garibaldi al 2...         store  
113331  VENTA EN SUBASTA - 31/08/2017-  12HS.VALOR BAS...         store  
76507    Los Surgentes, Córdoba - CÓDIGO 0433Excelente...         store  
54453   El inmueble esta emplazado sobre un terreno ir...         store  
...                                                   ...           ...  
115651  Casa en venta de 3 dormitorios  uno en suite ;...         house  
115656        Casa, General Paz, Ranchos, por U$S 220.000         house  
115658  Departamento en piso 10,  vista al frente con ...     apartment  
115677  Departamento de tres ambientes, con dos habita...     apartment  
115682  Se trata de un muy buen departamento en pleno ...     apartment  

[115604 rows x 13 columns]

In [102]:
q_price_usd_per_m2_deciles = pd.qcut(df_price_and_m2.price_usd_per_m2, 10)
q_price_usd_per_m2_deciles

0         (1083.333, 1372.058]
1         (1083.333, 1372.058]
2                          NaN
3         (2688.103, 3256.202]
4         (2688.103, 3256.202]
                  ...         
115683                     NaN
115684        (0.599, 637.505]
115685      (1600.0, 1822.222]
115686        (0.599, 637.505]
115687                     NaN
Name: price_usd_per_m2, Length: 115604, dtype: category
Categories (10, interval[float64]): [(0.599, 637.505] < (637.505, 1083.333] < (1083.333, 1372.058] < (1372.058, 1600.0] ... (2058.824, 2333.333] < (2333.333, 2688.103] < (2688.103, 3256.202] < (3256.202, 206333.333]]

In [103]:
# Comenzamos analizando las columnas surface_total_in_m2 y surface_covered_in_m2 en cuanto a minimos, máximos, mean, std;

df_price_and_m2.groupby(["state_name","property_type"]).agg(["mean", "min", "max", "std"])

price_usd_per_m2              \
                                                       mean         min   
state_name                   property_type                                
Bs.As. G.B.A. Zona Norte     PH                 1451.712566   49.485588   
                             apartment          2541.161161   31.246621   
                             house              1340.778935    4.166667   
                             store              1862.009755  158.730159   
Bs.As. G.B.A. Zona Oeste     PH                 1224.018825   77.893944   
                             apartment          1721.537324   20.898642   
                             house              1081.629587    7.000000   
                             store              1556.947316   28.041833   
Bs.As. G.B.A. Zona Sur       PH                 1114.012013   50.475300   
                             apartment          1890.569607   91.135875   
                             house              1164.503788   19.314341   
                             store              1541.024184   22.222222   
Buenos Aires Costa Atlántica PH                 1156.454370   55.000000   
                             apartment          1959.918157    1.000000   
                             house               749.149782    3.000000   
                             store              1401.045662   82.540833   
Buenos Aires Interior        PH                 1019.888682   45.824847   
                             apartment          1637.668972   15.160342   
                             house               643.020281    2.072029   
                             store               987.670901  133.928571   
Capital Federal              PH                 1695.517729  120.964706   
                             apartment          3324.516856   31.369688   
                             house              1547.041847  190.000000   
                             store              2899.667204   13.797467   
Córdoba                      PH                 1544.048178   36.601307   
                             apartment          1427.107194    1.184571   
                             house               710.948956   12.254902   
                             store              1458.775597   31.406853   
Santa Fe                     PH                 1207.188748  218.103167   
                             apartment          2392.245874    0.600000   
                             house               993.366830   37.916667   
                             store              3002.901146  416.666667   

                                                                        \
                                                      max          std   
state_name                   property_type                               
Bs.As. G.B.A. Zona Norte     PH              11333.333333   938.917931   
                             apartment       48296.222222  2387.838452   
                             house           38000.000000  1192.916414   
                             store           20833.333333  1819.141377   
Bs.As. G.B.A. Zona Oeste     PH              16000.000000  1159.268926   
                             apartment       24500.000000   883.977195   
                             house           80000.000000  2057.741767   
                             store           11818.181818  1627.518711   
Bs.As. G.B.A. Zona Sur       PH               2800.000000   490.746480   
                             apartment       23140.764706  1254.335635   
                             house            9411.764706   776.448121   
                             store           13000.000000  1524.366776   
Buenos Aires Costa Atlántica PH               5957.446809   554.608810   
                             apartment       21897.058824   816.024969   
                             house            5698.005128   535.291906   
                             store            4740.259740   953.937115   
Buenos Aire

In [104]:
# Dividimos los precios por M2 en intervalos para ver la concentración de la muestra.

price_intervalos = pd.interval_range(start=0, freq=1000, end=220000, closed='left')
price_categories = pd.cut(df["price_usd_per_m2"], bins = price_intervalos)

df.pivot_table('price_usd_per_m2', [price_categories], ['property_type'], fill_value='No existen', aggfunc='count')

property_type             PH   apartment       house       store
price_usd_per_m2                                                
[0, 1000)                812        1351        8916         493
[1000, 2000)            1783       15545        8472         692
[2000, 3000)             499       16997        1552         376
[3000, 4000)              32        4998         268         204
[4000, 5000)               3        1310          51          95
[5000, 6000)               3         571          33          66
[6000, 7000)               1         312          13          24
[7000, 8000)      No existen         104           7          18
[8000, 9000)               1          49          10          12
[9000, 10000)     No existen          45          11           3
[10000, 11000)             2          30           5           6
[11000, 12000)             2          11           3           2
[12000, 13000)    No existen          26           1           2
[13000, 14000)    No existen          50           3           4
[14000, 15000)             1          39           8           1
[15000, 16000)    No existen          31           8           2
[16000, 17000)             1          22           2           1
[17000, 18000)    No existen          58           3  No existen
[18000, 19000)    No existen          40           3           1
[19000, 20000)    No existen          39           2           1
[20000, 21000)    No existen          57           5           1
[21000, 22000)    No existen          69  No existen  No existen
[22000, 23000)    No existen          21  No existen           1
[23000, 24000)    No existen          74           1  No existen
[24000, 25000)    No existen          73  No existen  No existen
[25000, 26000)             1          48  No existen  No existen
[26000, 27000)    No existen           7           2  No existen
[27000, 28000)    No existen           6           1  No existen
[28000, 29000)    No existen           4  No existen  No existen
[29000, 30000)    No existen           1  No existen  No existen
[30000, 31000)             1           4           1  No existen
[31000, 32000)    No existen           6  No existen  No existen
[32000, 33000)    No existen          12  No existen  No existen
[33000, 34000)    No existen           4  No existen  No existen
[34000, 35000)    No existen           8  No existen  No existen
[35000, 36000)    No existen           3  No existen  No existen
[36000, 37000)    No existen           1           1  No existen
[37000, 38000)    No existen           3  No existen  No existen
[38000, 39000)    No existen           1           1  No existen
[39000, 40000)    No existen           4  No existen  No existen
[40000, 41000)    No existen           2  No existen  No existen
[42000, 43000)    No existen           3  No existen  No existen
[43000, 44000)    No existen           7  No existen  No existen
[44000, 45000)    No existen           6  No existen  No existen
[45000, 46000)    No existen           2  No existen  No existen
[48000, 49000)    No existen           3  No existen  No existen
[57000, 58000)    No existen  No existen  No existen           1
[78000, 79000)    No existen           1  No existen  No existen
[80000, 81000)    No existen  No existen           1  No existen
[104000, 105000)  No existen           1  No existen  No existen
[110000, 111000)           0           0           0           0
[173000, 174000)  No existen           1  No existen  No existen
[206000, 207000)  No existen           1  No existen  No existen

In [105]:
# No termina de cerrarnos lo que vemos en los dos análisis ateriores, por lo que empezamos a ver outliers y datos erróneos de precio en uss por m2;
df_price_and_m2_PH_Capital_Federal = df_price_and_m2.loc[(df_price_and_m2["property_type"] == "PH") & (df_price_and_m2["state_name"] == "Capital Federal"),:].sort_values("price_usd_per_m2", ascending = False)

df_price_and_m2_PH_Capital_Federal.shape

(1828, 6)

In [106]:
# Cantidad de nulos por property_type==PH & state_name==Capital Federal;
df_price_and_m2_PH_Capital_Federal_null = df_price_and_m2.loc[(df_price_and_m2["property_type"] == "PH") & (df_price_and_m2["state_name"] == "Capital Federal"),:].sort_values("price_usd_per_m2", ascending = False)["price_usd_per_m2"].isnull().sum()

df_price_and_m2_PH_Capital_Federal_null

562

In [107]:
# Calculamos proporción de nulos por property_type==PH & state_name==Capital Federal;
df_price_and_m2_PH_Capital_Federal_null / df_price_and_m2_PH_Capital_Federal.shape[0] *100

30.743982494529543

In [108]:
# Analizamos la cantidad total de registros donde la superficie cubierta es mayor a la superficie total;

df_price_and_m2.loc[(df_price_and_m2["surface_covered_in_m2"] > df_price_and_m2["surface_total_in_m2"]) & (df_price_and_m2["state_name"] == "Capital Federal"),:].shape

#Son 107 registros;

(105, 6)

In [109]:
# Segmentamos los que son registros que tienen mayor superficie cubierta que superficie total por tipo de propiedad, house;
df_price_and_m2.loc[(df_price_and_m2["surface_covered_in_m2"] > df_price_and_m2["surface_total_in_m2"]) & (df_price_and_m2["state_name"] == "Capital Federal") & (df_price_and_m2["property_type"] == "house"),:].shape

(31, 6)

In [110]:
#Quiero estar seguro de que está bien esto.

df[df.duplicated() == True]

state_name  rooms  price_usd_per_m2        lon        lat  \
53            Capital Federal    2.0       3447.753623 -58.438233 -34.565265   
83            Capital Federal    NaN       3440.000000        NaN        NaN   
117           Capital Federal    2.0       6481.481481 -58.361766 -34.617915   
137           Capital Federal    NaN       1531.250000        NaN        NaN   
291           Capital Federal    4.0               NaN -58.443087 -34.562188   
...                       ...    ...               ...        ...        ...   
115480  Buenos Aires Interior    NaN       1794.677556        NaN        NaN   
115481  Buenos Aires Interior    NaN       1200.000000        NaN        NaN   
115482  Buenos Aires Interior    NaN       1794.677556        NaN        NaN   
115550  Buenos Aires Interior    2.0               NaN -60.273716 -38.381390   
115650  Buenos Aires Interior    5.0        200.000000 -59.078922 -34.497174   

        surface_total_in_m2  price_aprox_usd  surface_covered_in_m2  \
53                     69.0        237895.00                   53.0   
83                    125.0        430000.00                  156.0   
117                    54.0        350000.00                   50.0   
137                   160.0        245000.00                  135.0   
291                   166.0              NaN                  152.0   
...                     ...              ...                    ...   
115480                 90.0        161520.98                   80.0   
115481                 90.0        108000.00                   80.0   
115482                 90.0        161520.98                   80.0   
115550                  NaN        115000.00                   63.0   
115650                250.0         50000.00                  200.0   

                place_name  geonames_id  \
53                Belgrano    3436077.0   
83         Capital Federal    3433955.0   
117          Puerto Madero    3429760.0   
137        Capital Federal    3433955.0   
291               Belgrano    3436077.0   
...                    ...          ...   
115480  General Pueyrredón    3433782.0   
115481  General Pueyrredón    3433782.0   
115482  General Pueyrredón    3433782.0   
115550        Tres Arroyos    3833857.0   
115650           Open Door    3430287.0   

                                                    title  \
53                                       Ultimas Unidades   
83      Casa 125m² con 3 Plantas en Lezica, Martín 300...   
117                   ZenCity 2 Amb piso ALTO! Vista RIO    
137     Casa 160m² con 3 Plantas en Marconi, Ing. 2400...   
291                                            VIEW POINT   
...                                                   ...   
115480  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...   
115481  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...   
115482  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...   
115550                 A ESTRENAR !!! Duplex de 2 dormit.   
115650                                         Casa venta   

                                              description property_type  
53      El edificio está situado en el barrio de  las ...     apartment  
83      Buena ubicaciÃ³n. Muy buen acceso. Lezica esq....         house  
117     En su dique 1, y delimitado por el Boulevard J...     apartment  
137     Duplex de buenisimas medidas ( 5X33) Hall de a...         house  
291     Inmejorable ubicación en  la esquina de Av. Li...     apartment  
...                                                   ...           ...  
115480  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...     apartment  
115481  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...     apartment  
115482  DEPARTAMENTO A ESTRENAR EN POZO LA PERLA METRO...     apartment  
115550  DEUPLEX DE 2, DORMIT. A ESTRENAR! Living-comed...     apartment  
115650  Venta sólo contado SIN FINANCIACIÓN. Casa fren...         house  

[4900 rows x 13 columns]

In [111]:
#Falta ver esto
df_price_and_m2[df_price_and_m2.duplicated(subset=["price_usd_per_m2", "surface_total_in_m2", "price_aprox_usd", "surface_covered_in_m2", "property_type", "state_name"]) == True]

price_usd_per_m2  surface_total_in_m2  price_aprox_usd  \
49                   NaN                 49.0              NaN   
53           3447.753623                 69.0         237895.0   
83           3440.000000                125.0         430000.0   
116          1775.000000                200.0         355000.0   
117          6481.481481                 54.0         350000.0   
...                  ...                  ...              ...   
115650        200.000000                250.0          50000.0   
115656               NaN                  NaN         220000.0   
115666               NaN                  NaN         170000.0   
115672        220.000000               1000.0         220000.0   
115682               NaN                  NaN          75000.0   

        surface_covered_in_m2 property_type             state_name  
49                       45.0     apartment        Capital Federal  
53                       53.0     apartment        Capital Federal  
83                      156.0         house        Capital Federal  
116                     178.0     apartment        Capital Federal  
117                      50.0     apartment        Capital Federal  
...                       ...           ...                    ...  
115650                  200.0         house  Buenos Aires Interior  
115656                    NaN         house  Buenos Aires Interior  
115666                  120.0     apartment  Buenos Aires Interior  
115672                  175.0         house  Buenos Aires Interior  
115682                    NaN     apartment  Buenos Aires Interior  

[30413 rows x 6 columns]

In [112]:
df_price_and_m2.groupby("state_name").sum()

price_usd_per_m2  surface_total_in_m2  \
state_name                                                            
Bs.As. G.B.A. Zona Norte          3.237676e+07            5853756.0   
Bs.As. G.B.A. Zona Oeste          6.240260e+06            1589880.0   
Bs.As. G.B.A. Zona Sur            9.415878e+06            1630029.0   
Buenos Aires Costa Atlántica      9.993586e+06            1482656.0   
Buenos Aires Interior             9.685576e+05            1233950.0   
Capital Federal                   7.303545e+07            3142906.0   
Córdoba                           4.476191e+06            2026399.0   
Santa Fe                          8.623376e+06             986225.0   

                              price_aprox_usd  surface_covered_in_m2  
state_name                                                            
Bs.As. G.B.A. Zona Norte         7.780630e+09              4117013.0  
Bs.As. G.B.A. Zona Oeste         1.227973e+09               985673.0  
Bs.As. G.B.A. Zona Sur           2.399033e+09              1583973.0  
Buenos Aires Costa Atlántica     1.296039e+09               818148.0  
Buenos Aires Interior            3.312582e+08               254566.0  
Capital Federal                  7.812374e+09              2671843.0  
Córdoba                          1.838641e+09              1230719.0  
Santa Fe                         7.552212e+08               557856.0

In [113]:
# DUDA --> ¿Cómo hacemos para comparar que los valores de la columna superficie total y siempre mayor a los valores de la columna superficie cubierta?

In [114]:
# Quiero saber cuántos NaN hay por state_name en la columna price_usd_per_m2;


df.groupby(["state_name", "property_type"])["price_usd_per_m2", "surface_total_in_m2", "price_aprox_usd", "surface_covered_in_m2", "price_aprox_local_currency"].std().sort_values("price_usd_per_m2", ascending=False)


C:\Users\Usuario\AppData\Local\Temp\ipykernel_21356\3707789311.py:4: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



KeyError: "Columns not found: 'price_aprox_local_currency'"

In [ ]:
df.pivot_table("price_usd_per_m2", "state_name", "property_type", aggfunc=["std", "mean", "min", "max"])

std                            \
property_type                          PH    apartment        house   
state_name                                                            
Bs.As. G.B.A. Zona Norte       938.917931  2387.647600  1192.540046   
Bs.As. G.B.A. Zona Oeste      1159.268926   884.332015  2057.741767   
Bs.As. G.B.A. Zona Sur         490.746480  1254.532586   776.448121   
Buenos Aires Costa Atlántica   554.608810   816.429473   535.291906   
Buenos Aires Interior          512.080247   517.445768   559.256520   
Capital Federal                887.360632  3892.824716  1654.290655   
Córdoba                       4070.615915   535.260531   777.244171   
Santa Fe                       406.055353  4330.735192  2103.129777   

                                                  mean               \
property_type                       store           PH    apartment   
state_name                                                            
Bs.As. G.B.A. Zona Norte      1819.141377  1451.712566  2539.871735   
Bs.As. G.B.A. Zona Oeste      1627.518711  1224.018825  1720.754481   
Bs.As. G.B.A. Zona Sur        1524.366776  1114.012013  1889.978782   
Buenos Aires Costa Atlántica   953.937115  1156.454370  1958.838430   
Buenos Aires Interior          610.157332  1019.888682  1633.999387   
Capital Federal               2222.673859  1695.517729  3324.464870   
Córdoba                        844.103398  1544.048178  1426.524689   
Santa Fe                      7963.224291  1207.188748  2391.993013   

                                                               min             \
property_type                       house        store          PH  apartment   
state_name                                                                      
Bs.As. G.B.A. Zona Norte      1339.764409  1862.009755   49.485588  29.906933   
Bs.As. G.B.A. Zona Oeste      1081.629587  1556.947316   77.893944  20.898642   
Bs.As. G.B.A. Zona Sur        1164.503788  1541.024184   50.475300  91.135875   
Buenos Aires Costa Atlántica   749.149782  1401.045662   55.000000   1.000000   
Buenos Aires Interior          643.236465   987.670901   45.824847  15.160342   
Capital Federal               1546.701574  2899.667204  120.964706  31.369688   
Córdoba                        713.335035  1458.775597   36.601307   1.184571   
Santa Fe                       990.905762  3002.901146  218.103167   0.600000   

                                                               max  \
property_type                      house       store            PH   
state_name                                                           
Bs.As. G.B.A. Zona Norte        4.166667  158.730159  11333.333333   
Bs.As. G.B.A. Zona Oeste        7.000000   28.041833  16000.000000   
Bs.As. G.B.A. Zona Sur         19.314341   22.222222   2800.000000   
Buenos Aires Costa Atlántica    3.000000   82.540833   5957.446809   
Buenos Aires Interior           2.072029  133.928571   1867.647059   
Capital Federal               190.000000   13.797467  25000.000000   
Córdoba                        12.254902   31.406853  30000.000000   
Santa Fe                        9.388501  416.666667   1724.573000   

                                                                         
property_type                     apartment         house         store  
state_name                                                               
Bs.As. G.B.A. Zona Norte       48296.222222  38000.000000  20833.333333  
Bs.As. G.B.A. Zona Oeste       24500.000000  80000.000000  11818.181818  
Bs.As. G.B.A. Zona Sur         23140.764706   9411.764706  13000.000000  
Buenos Aires Costa Atlántica   21897.058824   5698.005128   4740.259740  
Buenos Aires Interior           3657.142857   4166.666667   2333.333333  
Capital Federal               206333.333333  23064.516129  22000.000000  
Córdoba                        14960.000000  16666.666667   5521.472393  
Santa Fe                       44425.675676  36549.707237  57382.080000

In [ ]:
# Revisamos la composición del mix de propiedades dentro de cada provincia.

state_y_type_mix = (df.groupby(['state_name', 'property_type']))["price", "price_aprox_local_currency", "price_aprox_usd", "price_usd_per_m2", "surface_covered_in_m2", "surface_total_in_m2"]

df.pivot_table("price_usd_per_m2", index="state_name", columns=["state_name", "property_type"])


# state_y_type_mix.loc[:,["price", "price_aprox_local_currency", "price_aprox_usd", "price_usd_per_m2", "surface_covered_in_m2", "surface_total_in_m2"]]

C:\Users\Usuario\AppData\Local\Temp\ipykernel_16224\2535899502.py:3: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



state_name                   Bs.As. G.B.A. Zona Norte               \
property_type                                      PH    apartment   
state_name                                                           
Bs.As. G.B.A. Zona Norte                  1451.712566  2539.871735   
Bs.As. G.B.A. Zona Oeste                          NaN          NaN   
Bs.As. G.B.A. Zona Sur                            NaN          NaN   
Buenos Aires Costa Atlántica                      NaN          NaN   
Buenos Aires Interior                             NaN          NaN   
Capital Federal                                   NaN          NaN   
Córdoba                                           NaN          NaN   
Santa Fe                                          NaN          NaN   

state_name                                              \
property_type                       house        store   
state_name                                               
Bs.As. G.B.A. Zona Norte      1339.764409  1862.009755   
Bs.As. G.B.A. Zona Oeste              NaN          NaN   
Bs.As. G.B.A. Zona Sur                NaN          NaN   
Buenos Aires Costa Atlántica          NaN          NaN   
Buenos Aires Interior                 NaN          NaN   
Capital Federal                       NaN          NaN   
Córdoba                               NaN          NaN   
Santa Fe                              NaN          NaN   

state_name                   Bs.As. G.B.A. Zona Oeste               \
property_type                                      PH    apartment   
state_name                                                           
Bs.As. G.B.A. Zona Norte                          NaN          NaN   
Bs.As. G.B.A. Zona Oeste                  1224.018825  1720.754481   
Bs.As. G.B.A. Zona Sur                            NaN          NaN   
Buenos Aires Costa Atlántica                      NaN          NaN   
Buenos Aires Interior                             NaN          NaN   
Capital Federal                                   NaN          NaN   
Córdoba                                           NaN          NaN   
Santa Fe                                          NaN          NaN   

state_name                                             Bs.As. G.B.A. Zona Sur  \
property_type                       house        store                     PH   
state_name                                                                      
Bs.As. G.B.A. Zona Norte              NaN          NaN                    NaN   
Bs.As. G.B.A. Zona Oeste      1081.629587  1556.947316                    NaN   
Bs.As. G.B.A. Zona Sur                NaN          NaN            1114.012013   
Buenos Aires Costa Atlántica          NaN          NaN                    NaN   
Buenos Aires Interior                 NaN          NaN                    NaN   
Capital Federal                       NaN          NaN                    NaN   
Córdoba                               NaN          NaN                    NaN   
Santa Fe                              NaN          NaN                    NaN   

state_name                                 ... Capital Federal               \
property_type                   apartment  ...           house        store   
state_name                                 ...                                
Bs.As. G.B.A. Zona Norte              NaN  ...             NaN          NaN   
Bs.As. G.B.A. Zona Oeste              NaN  ...             NaN          NaN   
Bs.As. G.B.A. Zona Sur        1889.978782  ...             NaN          NaN   
Buenos Aires Costa Atlántica          NaN  ...             NaN          NaN   
Buenos Aires Interior                 NaN  ...             NaN          NaN   
Capital Federal                       NaN  ...     1546.701574  2899.667204   
Córdoba                               NaN  ...             NaN          NaN   
Santa Fe                              NaN  ...             NaN          NaN   

state_name                        Córdoba                

In [ ]:
df.head(3)

state_name  rooms  price_usd_per_m2        lon        lat  \
0  Capital Federal    NaN       1127.272727 -58.508839 -34.661824   
1  Capital Federal    NaN       1309.090909 -58.522982 -34.652262   
2  Capital Federal    NaN               NaN -58.516424 -34.647797   

   surface_total_in_m2  price_aprox_usd  price_aprox_local_currency    price  \
0                 55.0          62000.0                   1093959.0  62000.0   
1                 55.0          72000.0                   1270404.0  72000.0   
2                  NaN          95000.0                   1676227.5  95000.0   

   surface_covered_in_m2 place_name  geonames_id  \
0                   40.0  Mataderos    3430787.0   
1                   55.0  Mataderos    3430787.0   
2                    NaN    Liniers    3431333.0   

                                      title  \
0        2 AMB TIPO CASA SIN EXPENSAS EN PB   
1  2 AMB 3ER PISO CON ASCENSOR APTO CREDITO   
2              PH 3 amb. cfte. reciclado      

                                         description property_type  
0  2 AMBIENTES TIPO CASA PLANTA BAJA POR PASILLO,...            PH  
1  2 AMBIENTES 3ER PISO LATERAL LIVING COMEDOR AM...     apartment  
2  PH 3 ambientes con patio. Hay 3 deptos en lote...            PH

In [ ]:
df.groupby("state_name").sum()

floor    expenses    rooms  price_usd_per_m2  \
state_name                                                                     
Bs.As. G.B.A. Zona Norte       7147.0  12926104.0  21661.0      3.238687e+07   
Bs.As. G.B.A. Zona Oeste       2057.0   1756889.0  14329.0      6.240610e+06   
Bs.As. G.B.A. Zona Sur         1118.0   4287371.0   9420.0      9.416028e+06   
Buenos Aires Costa Atlántica    825.0    906538.0  22004.0      9.998920e+06   
Buenos Aires Interior            84.0    183488.0   3798.0      9.705104e+05   
Capital Federal               14165.0  41902139.0  41584.0      7.304215e+07   
Córdoba                        1950.0   3829720.0  16755.0      4.480915e+06   
Santa Fe                       2238.0   1930574.0  10017.0      8.625408e+06   

                                       lon            lat  \
state_name                                                  
Bs.As. G.B.A. Zona Norte     -6.709070e+05 -394168.331187   
Bs.As. G.B.A. Zona Oeste     -3.293698e+05 -194598.172284   
Bs.As. G.B.A. Zona Sur       -3.478982e+05 -207740.771305   
Buenos Aires Costa Atlántica -4.714543e+05 -310316.140925   
Buenos Aires Interior        -9.348831e+04  -57073.157595   
Capital Federal              -1.389029e+06 -822485.221406   
Córdoba                      -3.291815e+05 -161139.841850   
Santa Fe                     -3.266505e+05 -175822.377721   

                              surface_total_in_m2  price_aprox_usd  \
state_name                                                           
Bs.As. G.B.A. Zona Norte                5888821.0     7.802421e+09   
Bs.As. G.B.A. Zona Oeste                1593780.0     1.228612e+09   
Bs.As. G.B.A. Zona Sur                  1639034.0     2.399546e+09   
Buenos Aires Costa Atlántica            1492864.0     1.299341e+09   
Buenos Aires Interior                   1269373.0     3.324155e+08   
Capital Federal                         3151884.0     7.823345e+09   
Córdoba                                 2050506.0     1.840356e+09   
Santa Fe                                 997608.0     7.557069e+08   

                              price_aprox_local_currency         price  \
state_name                                                               
Bs.As. G.B.A. Zona Norte                    1.376698e+11  1.101509e+10   
Bs.As. G.B.A. Zona Oeste                    2.167825e+10  1.410931e+09   
Bs.As. G.B.A. Zona Sur                      4.233879e+10  2.932530e+09   
Buenos Aires Costa Atlántica                2.292623e+10  2.154183e+09   
Buenos Aires Interior                       5.865305e+09  6.040101e+08   
Capital Federal                             1.380390e+11  1.111251e+10   
Córdoba                                     3.247216e+10  8.484470e+09   
Santa Fe                                    1.333407e+10  6.211581e+09   

                              surface_covered_in_m2   geonames_id  
state_name                                                         
Bs.As. G.B.A. Zona Norte                  4279033.0  5.289845e+10  
Bs.As. G.B.A. Zona Oeste                  1030931.0  2.742407e+10  
Bs.As. G.B.A. Zona Sur                    1634320.0  3.267782e+10  
Buenos Aires Costa Atlántica               888034.0  3.088088e+10  
Buenos Aires Interior                      290854.0  7.794471e+09  
Capital Federal                           2931325.0  1.094785e+11  
Córdoba                                   1283796.0  4.633996e+10  
Santa Fe                                   592367.0  3.897947e+10

In [ ]:
df.groupby(["state_name","property_type"]).describe()

floor                        \
                                              count       mean        std   
state_name                   property_type                                  
Bs.As. G.B.A. Zona Norte     PH                14.0   1.714286   1.138729   
                             apartment       1623.0   4.380160   5.102793   
                             house          13364.0   0.000000   0.000000   
                             store             13.0   1.076923   0.277350   
Bs.As. G.B.A. Zona Oeste     PH                31.0   3.000000   2.280351   
                             apartment        535.0   3.661682   2.856678   
                             house           4663.0   0.000000   0.000000   
                             store              4.0   1.250000   0.500000   
Bs.As. G.B.A. Zona Sur       PH                24.0   2.166667   2.035910   
                             apartment        237.0   4.485232   3.496486   
                             house           6985.0   0.000000   0.000000   
                             store              2.0   1.500000   0.707107   
Buenos Aires Costa Atlántica PH                 6.0   3.000000   1.549193   
                             apartment        155.0   5.200000   4.484316   
                             house           2685.0   0.000000   0.000000   
                             store              1.0   1.000000        NaN   
Buenos Aires Interior        PH                 2.0   3.000000   2.828427   
                             apartment         21.0   3.619048   2.438774   
                             house           1325.0   0.000000   0.000000   
                             store              1.0   2.000000        NaN   
Capital Federal              PH               155.0   2.251613   2.211521   
                             apartment       2773.0   4.955283   4.337346   
                             house           2087.0   0.000000   0.000000   
                             store              8.0   9.375000  10.979689   
Córdoba                      PH               268.0   3.910448   2.959053   
                             apartment        344.0   2.587209   3.844417   
                             house           4521.0   0.000000   0.000000   
                             store              9.0   1.333333   0.500000   
Santa Fe                     PH                11.0   2.636364   1.911687   
                             apartment        470.0   4.678723   4.356816   
                             house           1924.0   0.000000   0.000000   
                             store              1.0  10.000000        NaN   

                                                                            \
                                             min    25%   50%    75%   max   
state_name                   property_type                                   
Bs.As. G.B.A. Zona Norte     PH              1.0   1.00   1.0   2.00   5.0   
                             apartment       1.0   1.00   3.0   5.00  50.0   
                             house           0.0   0.00   0.0   0.00   0.0   
                             store           1.0   1.00   1.0   1.00   2.0   
Bs.As. G.B.A. Zona Oeste     PH              1.0   1.00   2.0   4.00   9.0   
                             apartment       1.0   2.00   3.0   5.00  24.0   
                             house           0.0   0.00   0.0   0.00   0.0   
                             store           1.0   1.00   1.0   1.25   2.0   
Bs.As. G.B.A. Zona Sur       PH              1.0   1.00   1.5   2.25  10.0   
                             apartment       1.0   2.00   4.0   7.00  20.0   
                             house           0.0   0.00   0.0   0.00   0.0   
                             store           1.0   1.25   1.5   1.75   2.0   
Buenos Aires Costa Atlántica PH              2.0   2.00   2.5   3.00   6.0   
                             apartment       1.0   2.00   4.0   7.00  22.0   
                        

In [ ]:
min_surface_covered_in_m2 = df["surface_covered_in_m2"].min()
print("min_surface_covered_in_m2", min_surface_covered_in_m2)

max_surface_covered_in_m2 = df["surface_covered_in_m2"].max()
print("max_surface_covered_in_m2", max_surface_covered_in_m2)

mean_surface_covered_in_m2 = df["surface_covered_in_m2"].mean()
print("mean_surface_covered_in_m2", mean_surface_covered_in_m2)

min_surface_covered_in_m2 0.0
max_surface_covered_in_m2 187000.0
mean_surface_covered_in_m2 132.02095074736584


In [ ]:
#Estoy queriendo ver cuál es el dato que tiene este valor de superficie cubierta en m2 pero no estoy pudiendo dar en cómo hacerlo.
df.sort_values("surface_covered_in_m2", ascending=False)

state_name  floor  expenses  rooms  \
20644                Capital Federal    NaN   11000.0    NaN   
98185   Buenos Aires Costa Atlántica    NaN       NaN    2.0   
41436       Bs.As. G.B.A. Zona Norte    0.0       NaN    NaN   
48168       Bs.As. G.B.A. Zona Norte    NaN       NaN    NaN   
70553         Bs.As. G.B.A. Zona Sur    NaN       NaN    NaN   
...                              ...    ...       ...    ...   
115651         Buenos Aires Interior    0.0       NaN    NaN   
115656         Buenos Aires Interior    0.0       NaN    NaN   
115658         Buenos Aires Interior    NaN       NaN    NaN   
115677         Buenos Aires Interior    NaN       NaN    NaN   
115682         Buenos Aires Interior    NaN       NaN    NaN   

        price_usd_per_m2        lon        lat  surface_total_in_m2 currency  \
20644                NaN -58.409166 -34.594573                  NaN      USD   
98185        1423.076923 -57.547773 -37.989809                 52.0      USD   
41436         516.666667        NaN        NaN               1200.0      USD   
48168                NaN        NaN        NaN                 35.0      NaN   
70553          64.516129 -58.425045 -34.781917              93000.0      USD   
...                  ...        ...        ...                  ...      ...   
115651        300.925926 -57.902854 -34.922468                432.0      USD   
115656               NaN        NaN        NaN                  NaN      USD   
115658               NaN -62.270166 -38.712532                  NaN      USD   
115677       2373.913043        NaN        NaN                 92.0      USD   
115682               NaN -62.262843 -38.718968                  NaN      USD   

        price_aprox_usd  price_aprox_local_currency      price  \
20644          600000.0                  10586700.0   600000.0   
98185           74000.0                   1305693.0    74000.0   
41436          620000.0                  10939590.0   620000.0   
48168               NaN                         NaN        NaN   
70553         6000000.0                 105867000.0  6000000.0   
...                 ...                         ...        ...   
115651         130000.0                   2293785.0   130000.0   
115656         220000.0                   3881790.0   220000.0   
115658          78000.0                   1376271.0    78000.0   
115677         218400.0                   3853558.8   218400.0   
115682          75000.0                   1323337.5    75000.0   

        surface_covered_in_m2       place_name  geonames_id  \
20644                187000.0     Barrio Norte    3436109.0   
98185                 49000.0    Mar del Plata    3430863.0   
41436                 38240.0            Delta          NaN   
48168                 35000.0      Tortuguitas          NaN   
70553                 30000.0  Lomas de Zamora    3431270.0   
...                       ...              ...          ...   
115651                    NaN          Berisso    3436038.0   
115656                    NaN          Ranchos    3429610.0   
115658                    NaN     Bahía Blanca    3865084.0   
115677                    NaN            Luján    3430982.0   
115682                    NaN     Bahía Blanca    3865084.0   

                                                    title  \
20644                      Excelente PISO en Barrio Norte   
98185                      oportunidad frente al  mar!!!!   
41436   Casa 1200m² con 2 Plantas, Tigre, Delta, por U...   
48168                       Nave Industrial - Tortuguitas   
70553   LAVALLOL. Predio Industrial de 93.000 m2 y 30....   
...                                                   ...   
115651   Casa Amplia con Cochera y Dto interno con Patio    
115656                                     Casa - Ranchos   
115658                                     Caronti Nº 108   
115677                     Departamento - Centro De Lujan   
115682                          Venta dto 1 dorm céntrico   

             

In [ ]:
df.pivot_table("price_usd_per_m2", index="state_name", columns="property_type", aggfunc=["mean", "max", "min"])

mean                            \
property_type                          PH    apartment        house   
state_name                                                            
Bs.As. G.B.A. Zona Norte      1451.712566  2539.871735  1339.764409   
Bs.As. G.B.A. Zona Oeste      1224.018825  1720.754481  1081.629587   
Bs.As. G.B.A. Zona Sur        1114.012013  1889.978782  1164.503788   
Buenos Aires Costa Atlántica  1156.454370  1958.838430   749.149782   
Buenos Aires Interior         1019.888682  1633.999387   643.236465   
Capital Federal               1695.517729  3324.464870  1546.701574   
Córdoba                       1544.048178  1426.524689   713.335035   
Santa Fe                      1207.188748  2391.993013   990.905762   

                                                    max                 \
property_type                       store            PH      apartment   
state_name                                                               
Bs.As. G.B.A. Zona Norte      1862.009755  11333.333333   48296.222222   
Bs.As. G.B.A. Zona Oeste      1556.947316  16000.000000   24500.000000   
Bs.As. G.B.A. Zona Sur        1541.024184   2800.000000   23140.764706   
Buenos Aires Costa Atlántica  1401.045662   5957.446809   21897.058824   
Buenos Aires Interior          987.670901   1867.647059    3657.142857   
Capital Federal               2899.667204  25000.000000  206333.333333   
Córdoba                       1458.775597  30000.000000   14960.000000   
Santa Fe                      3002.901146   1724.573000   44425.675676   

                                                                 min  \
property_type                        house         store          PH   
state_name                                                             
Bs.As. G.B.A. Zona Norte      38000.000000  20833.333333   49.485588   
Bs.As. G.B.A. Zona Oeste      80000.000000  11818.181818   77.893944   
Bs.As. G.B.A. Zona Sur         9411.764706  13000.000000   50.475300   
Buenos Aires Costa Atlántica   5698.005128   4740.259740   55.000000   
Buenos Aires Interior          4166.666667   2333.333333   45.824847   
Capital Federal               23064.516129  22000.000000  120.964706   
Córdoba                       16666.666667   5521.472393   36.601307   
Santa Fe                      36549.707237  57382.080000  218.103167   

                                                                 
property_type                 apartment       house       store  
state_name                                                       
Bs.As. G.B.A. Zona Norte      29.906933    4.166667  158.730159  
Bs.As. G.B.A. Zona Oeste      20.898642    7.000000   28.041833  
Bs.As. G.B.A. Zona Sur        91.135875   19.314341   22.222222  
Buenos Aires Costa Atlántica   1.000000    3.000000   82.540833  
Buenos Aires Interior         15.160342    2.072029  133.928571  
Capital Federal               31.369688  190.000000   13.797467  
Córdoba                        1.184571   12.254902   31.406853  
Santa Fe                       0.600000    9.388501  416.666667

In [ ]:
df.pivot_table("price_usd_per_m2", ["state_name", "property_type"], columns="surface_covered_in_m2")

surface_covered_in_m2                           0.0          1.0      \
state_name                   property_type                             
Bs.As. G.B.A. Zona Norte     PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN  3021.995642   
                             store                  NaN          NaN   
Bs.As. G.B.A. Zona Oeste     PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN   712.080264   
                             store                  NaN          NaN   
Bs.As. G.B.A. Zona Sur       PH                     NaN  1046.444266   
                             apartment              NaN  1605.872247   
                             house                  NaN  1353.239659   
                             store                  NaN  1915.638724   
Buenos Aires Costa Atlántica PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store                  NaN          NaN   
Buenos Aires Interior        PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store                  NaN          NaN   
Capital Federal              PH                     NaN          NaN   
                             apartment      2467.788462          NaN   
                             house                  NaN  1662.629332   
                             store                  NaN          NaN   
Córdoba                      PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN   306.666667   
                             store                  NaN          NaN   
Santa Fe                     PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store                  NaN          NaN   

surface_covered_in_m2                           2.0          3.0      \
state_name                   property_type                             
Bs.As. G.B.A. Zona Norte     PH                     NaN          NaN   
                             apartment      2380.000000          NaN   
                             house                  NaN          NaN   
                             store                  NaN          NaN   
Bs.As. G.B.A. Zona Oeste     PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store           680.000000          NaN   
Bs.As. G.B.A. Zona Sur       PH                     NaN          NaN   
                             apartment      1463.414634          NaN   
                             house          1346.153846          NaN   
                             store                  NaN          NaN   
Buenos Aires Costa Atlántica PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store                  NaN          NaN   
Buenos Aires Interior        PH                     NaN          NaN   
                             apartment              NaN          NaN   
                             house                  NaN          NaN   
                             store     

In [ ]:
df.duplicated().sum()

4787